In [ ]:
from pyspark.sql.functions import lit
from pyspark.sql.types import *
from pyspark.sql.functions import col, count, rand, collect_list, explode, struct, count, lit
from pyspark.sql.functions import pandas_udf, PandasUDFType
import statistics
import pandas as pd
import numpy as np
from datetime import datetime

In [ ]:
# Aging date 
Ageing_date=datetime.strptime('2020-06-01',"%Y-%m-%d")

#Ranges
ranges=['low','mid','high']

In [ ]:
#Reading the reference table list table
ref_tables=sqlContext.sql("SELECT * FROM tr_us_market_base_db.ref_tables_list")
ref_tables=ref_tables.toPandas()

#Ageing table
aging = sqlContext.sql("SELECT * FROM tr_us_market_base_db.aging")
aging = aging.toPandas()

In [ ]:
#Levelling
def levelling(data,parameter):
    if parameter=='None':
      return(data)
    elif parameter=='TCC':
        colnames=[c for c in data.columns if 'Base' in c]
        pt=[item for subitem in colnames for item in subitem.split() if item.isdigit()]
        data['TCC Avg']=data.apply(lambda x: (x['TCC Avg']-x['Base Avg']) if (x['TCC Avg']-x['Base Avg'] > 0) else 0,axis=1)
    
        for i in pt:
            data['TCC '+str(i)+' p']=data.apply(lambda x: (x['TCC '+str(i)+' p']-x['Base '+str(i)+' p']) if (x['TCC '+str(i)+' p']-x['Base '+str(i)+' p'] > 0) else 0,axis=1)
    elif parameter=='TDC':
        colnames=[c for c in data.columns if 'Base' in c]
        pt=[item for subitem in colnames for item in subitem.split() if item.isdigit()]
        data['TDC Avg']=data.apply(lambda x: (x['TDC Avg']-x['Base Avg']) if (x['TDC Avg']-x['Base Avg'] > 0) else 0,axis=1)
        
        for i in pt:
            data['TDC '+str(i)+' p']=data.apply(lambda x: (x['TDC '+str(i)+' p']-x['Base '+str(i)+' p']) if (x['TDC '+str(i)+' p']-x['Base '+str(i)+' p'] > 0) else 0,axis=1)
    elif parameter=='both':
        colnames=[c for c in data.columns if 'Base' in c]
        pt=[item for subitem in colnames for item in subitem.split() if item.isdigit()]
        data['TDC Avg']=data.apply(lambda x: (x['TDC Avg']-x['TCC Avg']) if (x['TDC Avg']-x['TCC Avg'] > 0) else 0,axis=1)
        data['TCC Avg']=data.apply(lambda x: (x['TCC Avg']-x['Base Avg']) if (x['TCC Avg']-x['Base Avg'] > 0) else 0,axis=1)
        
        for i in pt:
            data['TDC '+str(i)+' p']=data.apply(lambda x: (x['TDC '+str(i)+' p']-x['TCC '+str(i)+' p']) if (x['TDC '+str(i)+' p']-x['TCC '+str(i)+' p'] > 0) else 0,axis=1)
            data['TCC '+str(i)+' p']=data.apply(lambda x: (x['TCC '+str(i)+' p']-x['Base '+str(i)+' p']) if (x['TCC '+str(i)+' p']-x['Base '+str(i)+' p'] > 0) else 0,axis=1)
    return(data)

  
def recalculate(data,parameter,ranges):
    if parameter=='None':
      return(data)
    
    elif parameter=='TCC':
        for j in ranges:
            colnames=[c for c in data.columns if 'Base' in c]
            colnames=[val.replace('.0','') for val in colnames]
            pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
            for i in pt:
                data['TCC_'+j+'_'+str(i)+'.0']=data['TCC_'+j+'_'+str(i)+'.0'] + data['Base_'+j+'_'+str(i)+'.0']
    elif parameter=='TDC':
        for j in ranges:
            colnames=[c for c in data.columns if 'Base' in c]
            colnames=[val.replace('.0','') for val in colnames]
            pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
            for i in pt:
                data['TDC_'+j+'_'+str(i)+'.0']=data['TDC_'+j+'_'+str(i)+'.0'] + data['Base_'+j+'_'+str(i)+'.0']
    elif parameter=='both':
        for j in ranges:
            colnames=[c for c in data.columns if 'Base' in c]
            colnames=[val.replace('.0','') for val in colnames]
            pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
            for i in pt:
                data['TDC_'+j+'_'+str(i)+'.0']=data['Base_'+j+'_'+str(i)+'.0'] + data['TCC_'+j+'_'+str(i)+'.0'] + data['TDC_'+j+'_'+str(i)+'.0']
                data['TCC_'+j+'_'+str(i)+'.0']=data['Base_'+j+'_'+str(i)+'.0'] + data['TCC_'+j+'_'+str(i)+'.0']
    
    return(data)

#Imputation
def imputation(data,parameter,ranges):
  if parameter=='None':
    return(data)
  
  elif parameter=='both':
    for j in ranges:
      colnames=[c for c in data.columns if 'Base' in c]
      colnames=[val.replace('.0','') for val in colnames]
      pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
      for i in pt:
        data['Flag TCC'+j+'_'+str(i)+'.0']=data.apply(lambda x: 1 if x['TCC_'+j+'_'+str(i)+'.0']==0 else 0,axis=1)
        data['TCC_'+j+'_'+str(i)+'.0']=data.apply(lambda x: x['Base_'+j+'_'+str(i)+'.0']*(x['TCC_'+j+'_'+str(i)+'.0_n']/x['Base_'+j+'_'+str(i)+'.0_n']) if x['TCC_'+j+'_'+str(i)+'.0']==0 else x['TCC_'+j+'_'+str(i)+'.0'],axis=1)
        
        data['Flag TDC'+j+'_'+str(i)+'.0']=data.apply(lambda x: 1 if x['TDC_'+j+'_'+str(i)+'.0']==0 else 0,axis=1)
        data['TDC_'+j+'_'+str(i)+'.0']=data.apply(lambda x: x['Base_'+j+'_'+str(i)+'.0']*(x['TDC_'+j+'_'+str(i)+'.0_n']/x['Base_'+j+'_'+str(i)+'.0_n']) if x['TDC_'+j+'_'+str(i)+'.0']==0 else x['TDC_'+j+'_'+str(i)+'.0'],axis=1)
  
    cols=[c for c in data.columns if 'Flag TCC' in c]
    data['Imputed TCC']=data[cols].sum(axis=1)
    data['Imputed TCC']=data['Imputed TCC'].apply(lambda x: 1 if x >0 else 0)
    data=data.drop(cols,axis=1)

    cols=[c for c in data.columns if 'Flag TDC' in c]
    data['Imputed TDC']=data[cols].sum(axis=1)
    data['Imputed TDC']=data['Imputed TDC'].apply(lambda x: 1 if x >0 else 0)
    data=data.drop(cols,axis=1)
  
  elif parameter=='TCC':
    for j in ranges:
      colnames=[c for c in data.columns if 'Base' in c]
      colnames=[val.replace('.0','') for val in colnames]
      pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
      for i in pt:
        data['Flag TCC'+j+'_'+str(i)+'.0']=data.apply(lambda x: 1 if x['TCC_'+j+'_'+str(i)+'.0']==0 else 0,axis=1)
        data['TCC_'+j+'_'+str(i)+'.0']=data.apply(lambda x: x['Base_'+j+'_'+str(i)+'.0']*(x['TCC_'+j+'_'+str(i)+'.0_n']/x['Base_'+j+'_'+str(i)+'.0_n']) if x['TCC_'+j+'_'+str(i)+'.0']==0 else x['TCC_'+j+'_'+str(i)+'.0'],axis=1)
  
    cols=[c for c in data.columns if 'Flag TCC' in c]
    data['Imputed TCC']=data[cols].sum(axis=1)
    data['Imputed TCC']=data['Imputed TCC'].apply(lambda x: 1 if x >0 else 0)
    data=data.drop(cols,axis=1)
  
  elif parameter=='TDC':
    for j in ranges:
      colnames=[c for c in data.columns if 'Base' in c]
      colnames=[val.replace('.0','') for val in colnames]
      pt=list(set([item for subitem in colnames for item in subitem.split('_') if item.isdigit()]))
      for i in pt:
        data['Flag TDC'+j+'_'+str(i)+'.0']=data.apply(lambda x: 1 if x['TDC_'+j+'_'+str(i)+'.0']==0 else 0,axis=1)
        data['TDC_'+j+'_'+str(i)+'.0']=data.apply(lambda x: x['Base_'+j+'_'+str(i)+'.0']*(x['TDC_'+j+'_'+str(i)+'.0_n']/x['Base_'+j+'_'+str(i)+'.0_n']) if x['TDC_'+j+'_'+str(i)+'.0']==0 else x['TDC_'+j+'_'+str(i)+'.0'],axis=1)
  
    cols=[c for c in data.columns if 'Flag TDC' in c]
    data['Imputed TDC']=data[cols].sum(axis=1)
    data['Imputed TDC']=data['Imputed TDC'].apply(lambda x: 1 if x >0 else 0)
    data=data.drop(cols,axis=1)
  
  return(data)


In [ ]:
#Moving files from DBFS to ADLS
#Mapping file
#dbutils.fs.mv('/FileStore/tables/Salaried_SC_Mapping.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

#Empsight
#dbutils.fs.mv('/FileStore/tables/EmpSight_Local_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')
#dbutils.fs.mv('/FileStore/tables/EmpSight_National_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

#WMG
#dbutils.fs.mv('/FileStore/tables/WMG_Local_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')
#dbutils.fs.mv('/FileStore/tables/WMG_National_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

#Mercer
#dbutils.fs.mv('/FileStore/tables/Mercer_Local_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')
#dbutils.fs.mv('/FileStore/tables/Mercer_National_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

#Kornferry
#dbutils.fs.mv('/FileStore/tables/KF_Local_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')
#dbutils.fs.mv('/FileStore/tables/KF_National_SC.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

In [ ]:
# show files in a folder
#dbutils.fs.ls("/mnt/totalrewards/dev/adhoc/a0a025e")

In [ ]:
#Reading files from ADLS into dataframe
#Empsight
Empsight_local_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/EmpSight_Local_SC.csv")
#dbutils.fs.mv('/FileStore/tables/Salaried_SC_Mapping.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

Empsight_national_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/EmpSight_National_SC.csv")

Empsight_local_SC = Empsight_local_SC.withColumn('TableNbr', lit(7))
Empsight_national_SC = Empsight_national_SC.withColumn('TableNbr', lit(8))

Empsight_local_SC = Empsight_local_SC.toPandas()
Empsight_national_SC = Empsight_national_SC.toPandas()

In [ ]:
#WMG
WMG_local_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/WMG_Local_SC.csv")

WMG_national_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/WMG_National_SC.csv")

WMG_local_SC = WMG_local_SC.withColumn('TableNbr', lit(9))
WMG_national_SC = WMG_national_SC.withColumn('TableNbr', lit(10))

WMG_local_SC = WMG_local_SC.toPandas()
WMG_national_SC = WMG_national_SC.toPandas()

In [ ]:
#Mercer
Mercer_local_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Mercer_Local_SC.csv")

Mercer_national_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Mercer_National_SC.csv")

Mercer_local_SC = Mercer_local_SC.withColumn('TableNbr', lit(4))
Mercer_national_SC = Mercer_national_SC.withColumn('TableNbr', lit(6))

Mercer_local_SC = Mercer_local_SC.toPandas()
Mercer_national_SC = Mercer_national_SC.toPandas()


In [ ]:
#Kornferry
KF_local_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/KF_Local_SC.csv")

KF_national_SC = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/KF_National_SC.csv")

KF_local_SC = KF_local_SC.withColumn('TableNbr', lit(1))
KF_national_SC = KF_national_SC.withColumn('TableNbr', lit(5))

KF_local_SC = KF_local_SC.toPandas()
KF_national_SC = KF_national_SC.toPandas()


In [ ]:
#Mapping file
Mapping = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Salaried_SC_Mapping.csv")

Mapping = Mapping.toPandas()


In [ ]:
Mapping.head()

tgt_job_family 
 tgt_column_name 
 src_table_nbr 
 src_column 
 src_table_name 
 
 
 
 
 0 
 Supply Chain 
 Job Code 
 7 
 JobCode 
 empsight 
 
 
 1 
 Supply Chain 
 Location 
 7 
 EmpsightSurveyGeography 
 empsight 
 
 
 2 
 Supply Chain 
 Survey Release Date 
 7 
 SurveyReleaseDate 
 empsight 
 
 
 3 
 Supply Chain 
 Base Emp 
 7 
 AnnualBaseIncs 
 empsight 
 
 
 4 
 Supply Chain 
 Base Avg 
 7 
 AnnualBaseAverage 
 empsight

In [ ]:
#Empsight local
#Subsetting only required columns from data and renaming the columns
Mapping_empsight_local = Mapping[Mapping['src_table_nbr']==Empsight_local_SC['TableNbr'].iloc[0]]

Empsight_local = Empsight_local_SC[list(Mapping_empsight_local.to_dict()['src_column'].values())]
Empsight_local.head()

src_list = list(Mapping_empsight_local['src_column'])
tgt_list = list(Mapping_empsight_local['tgt_column_name'])

Mapping_empsight_local_dict = dict(zip(src_list,tgt_list))

Empsight_local = Empsight_local.rename(columns=Mapping_empsight_local_dict)
Empsight_local['TableNbr'] = 7

Empsight_local.head()

Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 ... 
 TCC 75 p 
 TCC 90 p 
 TDC Emp 
 TDC Avg 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TableNbr 
 
 
 
 
 0 
 CEOW-X2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 6 
 1.383333e+06 
 NaN 
 775000.0 
 1125000.04 
 2250000.0 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 1 
 COOP-X1 
 New York- Northern NJ-Long Island 
 3/1/2019 
 5 
 7.087740e+05 
 NaN 
 NaN 
 600000.00 
 NaN 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 2 
 CEOS-V2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 6 
 6.670000e+05 
 NaN 
 NaN 
 622500.00 
 NaN 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 3 
 CINV-V2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 5 
 6.102500e+05 
 NaN 
 NaN 
 550000.00 
 NaN 
 NaN 
 ... 
 NaN 
 NaN 
 5.0 
 3205526.573 
 NaN 
 NaN 
 2915517.22 
 NaN 
 NaN 
 7 
 
 
 4 
 CLGC-V3 
 Boston-Worcester-Lawrence-Lowell 
 3/1/2019 
 5 
 4.680001e+05 
 NaN 
 NaN 
 400000.12 
 NaN 
 NaN 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 
 5 rows × 25 columns

In [ ]:
#Empsight national
#Subsetting only required columns from data and renaming the columns
Mapping_empsight_national = Mapping[Mapping['src_table_nbr']==Empsight_national_SC['TableNbr'].iloc[0]]

Empsight_national = Empsight_national_SC[list(Mapping_empsight_national.to_dict()['src_column'].values())]
Empsight_national.head()

src_list = list(Mapping_empsight_national['src_column'])
tgt_list = list(Mapping_empsight_national['tgt_column_name'])

Mapping_empsight_national_dict = dict(zip(src_list,tgt_list))

Empsight_national = Empsight_national.rename(columns=Mapping_empsight_national_dict)
Empsight_national['TableNbr'] = 8

Empsight_national.head()

Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 ... 
 TCC 75 p 
 TCC 90 p 
 TDC Emp 
 TDC Avg 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TableNbr 
 
 
 
 
 0 
 CEOC-X2 
 National 
 3/1/2019 
 34 
 1.372792e+06 
 1000000.0000 
 1.100000e+06 
 1.287500e+06 
 1.550000e+06 
 1.810000e+06 
 ... 
 3900000.000 
 5147500.234 
 34.0 
 1.272879e+07 
 4200771.956 
 7.752150e+06 
 1.288612e+07 
 1.655060e+07 
 2.184036e+07 
 8 
 
 
 1 
 CEOW-X2 
 National 
 3/1/2019 
 27 
 1.245650e+06 
 900000.0000 
 9.662500e+05 
 1.000002e+06 
 1.342849e+06 
 2.020068e+06 
 ... 
 3365625.000 
 3562205.640 
 27.0 
 7.556047e+06 
 1760000.000 
 3.399940e+06 
 7.523983e+06 
 9.390172e+06 
 1.645524e+07 
 8 
 
 
 2 
 COOP-X1 
 National 
 3/1/2019 
 36 
 8.077947e+05 
 353999.9991 
 5.500000e+05 
 6.750000e+05 
 9.146875e+05 
 1.297500e+06 
 ... 
 2034688.872 
 3438815.600 
 36.0 
 4.139303e+06 
 505000.000 
 1.514792e+06 
 2.735335e+06 
 6.195178e+06 
 7.415490e+06 
 8 
 
 
 3 
 COOS-V2 
 National 
 3/1/2019 
 10 
 3.589805e+05 
 218276.0087 
 2.295936e+05 
 3.934099e+05 
 4.516667e+05 
 4.826667e+05 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 8 
 
 
 4 
 CCOF-V3 
 National 
 3/1/2019 
 8 
 5.403750e+05 
 NaN 
 3.955000e+05 
 4.590000e+05 
 7.250000e+05 
 NaN 
 ... 
 1112187.504 
 NaN 
 8.0 
 2.042833e+06 
 NaN 
 9.327140e+05 
 1.804191e+06 
 2.807994e+06 
 NaN 
 8 
 
 
 
 5 rows × 25 columns

In [ ]:
#WMG local
#Subsetting only required columns from data and renaming the columns
Mapping_WMG_local = Mapping[Mapping['src_table_nbr']==WMG_local_SC['TableNbr'].iloc[0]]

WMG_local = WMG_local_SC[list(Mapping_WMG_local.to_dict()['src_column'].values())]
WMG_local.head()

src_list = list(Mapping_WMG_local['src_column'])
tgt_list = list(Mapping_WMG_local['tgt_column_name'])

Mapping_WMG_local_dict = dict(zip(src_list,tgt_list))

WMG_local = WMG_local.rename(columns=Mapping_WMG_local_dict)
WMG_local['TableNbr'] = 9

WMG_local.head()

TCC 90 p 
 Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 TCC Emp 
 TCC Avg 
 TCC 10 p 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TableNbr 
 
 
 
 
 0 
 NaN 
 ADS-A1 
 AL Alabama-Other 
 2019-08-11 
 23 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 23 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 1 
 NaN 
 ADS-A1 
 AR Little Rock 
 2019-08-11 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 2 
 NaN 
 ADS-A1 
 AZ Phoenix Metro 
 2019-08-11 
 12 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 12 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 3 
 NaN 
 ADS-A1 
 CA California-Other 
 2019-08-11 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 4 
 NaN 
 ADS-A1 
 CA Central Coast 
 2019-08-11 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9

In [ ]:
#Cleaning the location
WMG_local[['State','Location1']]=WMG_local['Location'].str.split(" ",1,expand=True)

WMG_local['Location1']=WMG_local['Location1'].str.replace('-Other','')
WMG_local['Location1']=WMG_local['Location1'].str.replace(' Other','')
WMG_local['Location1']=WMG_local['Location1'].str.replace(' Metro','')

WMG_local['Location']=WMG_local[['Location1','State']].apply(lambda x: ','.join(x),axis=1)
WMG_local.drop(['Location1','State'],inplace=True,axis=1)
WMG_local.head()

TCC 90 p 
 Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 TCC Emp 
 TCC Avg 
 TCC 10 p 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TableNbr 
 
 
 
 
 0 
 NaN 
 ADS-A1 
 Alabama,AL 
 2019-08-11 
 23 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 23 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 1 
 NaN 
 ADS-A1 
 Little Rock,AR 
 2019-08-11 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 2 
 NaN 
 ADS-A1 
 Phoenix,AZ 
 2019-08-11 
 12 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 12 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 3 
 NaN 
 ADS-A1 
 California,CA 
 2019-08-11 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 
 
 4 
 NaN 
 ADS-A1 
 Central Coast,CA 
 2019-08-11 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9

In [ ]:
#WMG national
#Subsetting only required columns from data and renaming the columns
Mapping_WMG_national = Mapping[Mapping['src_table_nbr']==WMG_national_SC['TableNbr'].iloc[0]]

WMG_national = WMG_national_SC[list(Mapping_WMG_national.to_dict()['src_column'].values())]
WMG_national.head()

src_list = list(Mapping_WMG_national['src_column'])
tgt_list = list(Mapping_WMG_national['tgt_column_name'])

Mapping_WMG_national_dict = dict(zip(src_list,tgt_list))

WMG_national = WMG_national.rename(columns=Mapping_WMG_national_dict)
WMG_national['TableNbr'] = 10

WMG_national.head()

Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 TCC Emp 
 TCC Avg 
 TCC 10 p 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TCC 90 p 
 TableNbr 
 
 
 
 
 0 
 ADS-A1 
 National 
 2019-08-11 
 760 
 35528.9269 
 27414.40 
 30680.00 
 34918.208 
 40181.44 
 47758.048 
 760 
 35918.4595 
 27414.40 
 30680.00 
 34923.20 
 40206.400 
 47864.9600 
 10 
 
 
 1 
 ADS-A3 
 National 
 2019-08-11 
 3226 
 38582.2403 
 29120.00 
 32240.00 
 37440.000 
 43680.00 
 48318.400 
 3226 
 39011.3575 
 29120.00 
 32282.00 
 37627.20 
 43784.000 
 48443.2000 
 10 
 
 
 2 
 ADS-A4 
 National 
 2019-08-11 
 606 
 44635.2387 
 30264.00 
 36400.00 
 44220.800 
 50960.00 
 56804.800 
 606 
 45164.4452 
 30264.00 
 36400.00 
 44220.80 
 51126.400 
 56863.4955 
 10 
 
 
 3 
 ADS-A5 
 National 
 2019-08-11 
 77 
 49564.2390 
 37128.00 
 42369.60 
 47465.600 
 49878.40 
 62400.000 
 77 
 50589.8910 
 37128.00 
 42369.60 
 47465.60 
 49878.400 
 62400.0000 
 10 
 
 
 4 
 ADS-M0 
 National 
 2019-08-11 
 12 
 57680.3177 
 48000.16 
 49419.24 
 55650.000 
 61519.12 
 67054.000 
 12 
 60882.3166 
 48000.16 
 49419.24 
 55764.91 
 65817.045 
 77112.1000 
 10

In [ ]:
#Mercer local
#Subsetting only required columns from data and renaming the columns
Mapping_mercer_local = Mapping[Mapping['src_table_nbr']==Mercer_local_SC['TableNbr'].iloc[0]]

Mercer_local = Mercer_local_SC[list(Mapping_mercer_local.to_dict()['src_column'].values())]
Mercer_local.head()

src_list = list(Mapping_mercer_local['src_column'])
tgt_list = list(Mapping_mercer_local['tgt_column_name'])

Mapping_mercer_local_dict = dict(zip(src_list,tgt_list))

Mercer_local = Mercer_local.rename(columns=Mapping_mercer_local_dict)
Mercer_local['TableNbr'] = 4

Mercer_local.head()

TDC Avg 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 TCC Emp 
 TCC Avg 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TDC Emp 
 TableNbr 
 
 
 
 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 AFS.05.000.M10 
 Kansas City, Missouri 
 3/1/2019 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 4 
 
 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 AFS.05.000.M10 
 North Central 
 3/1/2019 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 4 
 
 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 AFS.05.000.M10 
 Kansas 
 3/1/2019 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 4 
 
 
 3 
 NaN 
 NaN 
 NaN 
 NaN 
 AFS.05.000.M20 
 Columbia, South Carolina 
 3/1/2019 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 4 
 
 
 4 
 NaN 
 NaN 
 NaN 
 NaN 
 AFS.05.000.M20 
 Dayton, Ohio 
 3/1/2019 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 1 
 4

In [ ]:
#Mercer national
#Subsetting only required columns from data and renaming the columns
Mapping_mercer_national = Mapping[Mapping['src_table_nbr']==Mercer_national_SC['TableNbr'].iloc[0]]

Mercer_national = Mercer_national_SC[list(Mapping_mercer_national.to_dict()['src_column'].values())]
Mercer_national.head()

src_list = list(Mapping_mercer_national['src_column'])
tgt_list = list(Mapping_mercer_national['tgt_column_name'])

Mapping_mercer_national_dict = dict(zip(src_list,tgt_list))

Mercer_national = Mercer_national.rename(columns=Mapping_mercer_national_dict)
Mercer_national['TableNbr'] = 6

Mercer_national.head()

Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 TCC Emp 
 TCC Avg 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TDC Emp 
 TDC Avg 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TableNbr 
 
 
 
 
 0 
 AFS.05.000.M10 
 National 
 2019-03-01 
 4 
 NaN 
 NaN 
 NaN 
 NaN 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 6 
 
 
 1 
 AFS.05.000.M20 
 National 
 2019-03-01 
 57 
 70126.0 
 NaN 
 62300.0 
 NaN 
 56 
 72948.0 
 NaN 
 63550.0 
 NaN 
 56 
 72948.0 
 NaN 
 63550.0 
 NaN 
 6 
 
 
 2 
 AFS.05.000.M30 
 National 
 2019-03-01 
 186 
 85041.0 
 71400.0 
 81181.0 
 94386.0 
 186 
 91520.0 
 72375.0 
 82000.0 
 106631.0 
 186 
 92394.0 
 72375.0 
 82000.0 
 109704.0 
 6 
 
 
 3 
 AFS.05.000.M40 
 National 
 2019-03-01 
 112 
 118500.0 
 NaN 
 109485.0 
 NaN 
 102 
 129433.0 
 NaN 
 116172.0 
 NaN 
 102 
 131700.0 
 NaN 
 116172.0 
 NaN 
 6 
 
 
 4 
 AFS.05.000.M50 
 National 
 2019-03-01 
 6 
 198536.0 
 NaN 
 199191.0 
 NaN 
 6 
 247729.0 
 NaN 
 247904.0 
 NaN 
 6 
 253581.0 
 NaN 
 247904.0 
 NaN 
 6

In [ ]:
#Kornferry local
#Subsetting only required columns from data and renaming the columns
Mapping_KF_local = Mapping[Mapping['src_table_nbr']==KF_local_SC['TableNbr'].iloc[0]]

KF_local = KF_local_SC[list(Mapping_KF_local.to_dict()['src_column'].values())]
KF_local.head()

src_list = list(Mapping_KF_local['src_column'])
tgt_list = list(Mapping_KF_local['tgt_column_name'])

Mapping_KF_local_dict = dict(zip(src_list,tgt_list))

KF_local = KF_local.rename(columns=Mapping_KF_local_dict)
KF_local['TableNbr'] = 1

KF_local.head()

TCC Emp 
 TCC Avg 
 TCC 10 p 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TCC 90 p 
 Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 TableNbr 
 
 
 
 
 0 
 145 
 15.64767644 
 11.07341346 
 12.48161058 
 13.73918269 
 17.69807692 
 21.40942308 
 3769, 3779, 1183 
 Akron 
 5/1/2019 
 333 
 13.536533 
 11.40038462 
 12.17019231 
 12.65714808 
 14.55769231 
 16.54652837 
 1 
 
 
 1 
 81 
 34.16386202 
 29.43639423 
 30.37572115 
 32.73305288 
 37.96887019 
 41.04298077 
 3800, 3802, 1182 
 Albany-Schenectady-Troy 
 5/1/2019 
 81 
 31.617620 
 26.98245192 
 28.29302885 
 29.51778846 
 34.55342548 
 39.08846154 
 1 
 
 
 2 
 81 
 34.16386202 
 29.43639423 
 30.37572115 
 32.73305288 
 37.96887019 
 41.04298077 
 3800, 3802, 1182 
 Albany-Schenectady-Troy 
 5/1/2019 
 81 
 31.617620 
 26.98245192 
 28.29302885 
 29.51778846 
 34.55342548 
 39.08846154 
 1 
 
 
 3 
 81 
 34.16386202 
 29.43639423 
 30.37572115 
 32.73305288 
 37.96887019 
 41.04298077 
 3800, 3802, 1182 
 Albany-Schenectady-Troy 
 5/1/2019 
 81 
 31.617620 
 26.98245192 
 28.29302885 
 29.51778846 
 34.55342548 
 39.08846154 
 1 
 
 
 4 
 59 
 15.14685481 
 12.03942308 
 12.64471154 
 14.38509615 
 16.33333317 
 19.1217149 
 3769, 3779, 1183 
 Albany-Schenectady-Troy 
 5/1/2019 
 375 
 15.141972 
 12.07884615 
 14.35 
 14.75 
 16 
 18.6 
 1

In [ ]:
#Kornferry national
#Subsetting only required columns from data and renaming the columns
Mapping_KF_national = Mapping[Mapping['src_table_nbr']==KF_national_SC['TableNbr'].iloc[0]]

KF_national = KF_national_SC[list(Mapping_KF_national.to_dict()['src_column'].values())]
KF_national.head()

src_list = list(Mapping_KF_national['src_column'])
tgt_list = list(Mapping_KF_national['tgt_column_name'])

Mapping_KF_national_dict = dict(zip(src_list,tgt_list))

KF_national = KF_national.rename(columns=Mapping_KF_national_dict)
KF_national['TableNbr'] = 5

KF_national.head()

Job Code 
 Location 
 Survey Release Date 
 Base Emp 
 Base Avg 
 Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 TCC Emp 
 TCC Avg 
 TCC 10 p 
 TCC 25 p 
 TCC 50 p 
 TCC 75 p 
 TCC 90 p 
 TableNbr 
 
 
 
 
 0 
 3763, 3773 
 National 
 2019-05-01 
 47 
 77.212247 
 58.9384615384615 
 71.06875 
 78.692308 
 86.3127403846154 
 93.1495192307692 
 46 
 96.0168802884615 
 70.5392307692308 
 87.5582932692308 
 95.878125 
 110.082572115385 
 121.137932692308 
 5 
 
 
 1 
 3763, 3773 
 National 
 2019-05-01 
 46 
 79.818056 
 65.3615384615385 
 71.4944711538461 
 79.987500 
 86.6659855769231 
 93.1829326923077 
 45 
 99.7751697115385 
 79.6174038461538 
 88.375 
 97.5394230769231 
 110.808653846154 
 121.181346153846 
 5 
 
 
 2 
 3763, 3773 
 National 
 2019-05-01 
 46 
 79.818056 
 65.3615384615385 
 71.4944711538461 
 79.987500 
 86.6659855769231 
 93.1829326923077 
 45 
 99.7751697115385 
 79.6174038461538 
 88.375 
 97.5394230769231 
 110.808653846154 
 121.181346153846 
 5 
 
 
 3 
 3799, 3801 
 National 
 2019-05-01 
 141 
 71.396961 
 46.2097754807692 
 59.6714745192308 
 72.000000 
 84.1346153846154 
 94.1620192307692 
 106 
 86.0497230769231 
 49.8732370192308 
 71.0653846153846 
 86.7519230769231 
 103.775561057692 
 112.796826923077 
 5 
 
 
 4 
 3799, 3801 
 National 
 2019-05-01 
 128 
 70.754187 
 46.2097754807692 
 59 
 72.000000 
 84.1346153846154 
 93.75 
 98 
 86.0326956730769 
 * 
 69.1139423076923 
 88.0985576923077 
 104.099559134615 
 * 
 5

In [ ]:
#Creating one table for all surveys
SC_Merged_Local = pd.concat([Empsight_local,WMG_local,Mercer_local,KF_local])
SC_Merged_National = pd.concat([Empsight_national,WMG_national,Mercer_national,KF_national])

In [ ]:
SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TCC Avg 
 TCC Emp 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 
 
 
 
 0 
 NaN 
 775000 
 1.125e+06 
 2.25e+06 
 NaN 
 1.383333e+06 
 6 
 CEOW-X2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 1 
 NaN 
 NaN 
 600000 
 NaN 
 NaN 
 7.087740e+05 
 5 
 COOP-X1 
 New York- Northern NJ-Long Island 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 2 
 NaN 
 NaN 
 622500 
 NaN 
 NaN 
 6.670000e+05 
 6 
 CEOS-V2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 3 
 NaN 
 NaN 
 550000 
 NaN 
 NaN 
 6.102500e+05 
 5 
 CINV-V2 
 New York- Northern NJ-Long Island 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 2915517.22 
 NaN 
 NaN 
 3205526.573 
 5.0 
 7 
 
 
 4 
 NaN 
 NaN 
 400000 
 NaN 
 NaN 
 4.680001e+05 
 5 
 CLGC-V3 
 Boston-Worcester-Lawrence-Lowell 
 3/1/2019 
 ... 
 855550 
 5.0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 
 
 
 5 rows × 25 columns

In [ ]:
SC_Merged_National.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TCC Avg 
 TCC Emp 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 
 
 
 
 0 
 1e+06 
 1.1e+06 
 1.287500e+06 
 1.55e+06 
 1.81e+06 
 1.372792e+06 
 34 
 CEOC-X2 
 National 
 3/1/2019 
 ... 
 3.47394e+06 
 20.0 
 4200771.956 
 7.752150e+06 
 1.288612e+07 
 1.655060e+07 
 2.184036e+07 
 1.272879e+07 
 34.0 
 8 
 
 
 1 
 900000 
 966250 
 1.000002e+06 
 1.34285e+06 
 2.02007e+06 
 1.245650e+06 
 27 
 CEOW-X2 
 National 
 3/1/2019 
 ... 
 2.97529e+06 
 23.0 
 1760000.000 
 3.399940e+06 
 7.523983e+06 
 9.390172e+06 
 1.645524e+07 
 7.556047e+06 
 27.0 
 8 
 
 
 2 
 354000 
 550000 
 6.750000e+05 
 914688 
 1.2975e+06 
 8.077947e+05 
 36 
 COOP-X1 
 National 
 3/1/2019 
 ... 
 1.93684e+06 
 26.0 
 505000.000 
 1.514792e+06 
 2.735335e+06 
 6.195178e+06 
 7.415490e+06 
 4.139303e+06 
 36.0 
 8 
 
 
 3 
 218276 
 229594 
 3.934099e+05 
 451667 
 482667 
 3.589805e+05 
 10 
 COOS-V2 
 National 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 8 
 
 
 4 
 NaN 
 395500 
 4.590000e+05 
 725000 
 NaN 
 5.403750e+05 
 8 
 CCOF-V3 
 National 
 3/1/2019 
 ... 
 884686 
 7.0 
 NaN 
 9.327140e+05 
 1.804191e+06 
 2.807994e+06 
 NaN 
 2.042833e+06 
 8.0 
 8 
 
 
 
 5 rows × 25 columns

In [ ]:
#Data Cleaning
SC_Merged_Local=SC_Merged_Local.replace(r'\*',np.nan,regex=True)
SC_Merged_Local=SC_Merged_Local.replace(r'\#',np.nan,regex=True)

cols = [i for i in SC_Merged_Local.columns if i not in ["Job Code", "Location", "Survey Release Date", "TableNbr"]]
SC_Merged_Local[cols] = SC_Merged_Local[cols].apply(pd.to_numeric)

SC_Merged_Local.dtypes

Out[ 25 ]: Base 10 p float64
Base 25 p float64
Base 50 p float64
Base 75 p float64
Base 90 p float64
Base Avg float64
Base Emp int32
Job Code object
Location object
Survey Release Date object
TCC 10 p float64
TCC 25 p float64
TCC 50 p float64
TCC 75 p float64
TCC 90 p float64
TCC Avg float64
TCC Emp float64
TDC 10 p float64
TDC 25 p float64
TDC 50 p float64
TDC 75 p float64
TDC 90 p float64
TDC Avg float64
TDC Emp float64
TableNbr int64
dtype: object

In [ ]:
#Data Cleaning
SC_Merged_National=SC_Merged_National.replace(r'\*',np.nan,regex=True)
SC_Merged_National=SC_Merged_National.replace(r'\#',np.nan,regex=True)

cols = [i for i in SC_Merged_National.columns if i not in ["Job Code", "Location", "Survey Release Date", "TableNbr"]]
SC_Merged_National[cols] = SC_Merged_National[cols].apply(pd.to_numeric)

SC_Merged_National.dtypes

Out[ 26 ]: Base 10 p float64
Base 25 p float64
Base 50 p float64
Base 75 p float64
Base 90 p float64
Base Avg float64
Base Emp int32
Job Code object
Location object
Survey Release Date object
TCC 10 p float64
TCC 25 p float64
TCC 50 p float64
TCC 75 p float64
TCC 90 p float64
TCC Avg float64
TCC Emp float64
TDC 10 p float64
TDC 25 p float64
TDC 50 p float64
TDC 75 p float64
TDC 90 p float64
TDC Avg float64
TDC Emp float64
TableNbr int64
dtype: object

In [ ]:
#df1=SC_Merged_Local

In [ ]:

#df1=df1['Location'].unique()
#df1=pd.DataFrame(df1)
#type(df1)
#df1.columns=['Location']
#df1.head()

In [ ]:
#dfs=sqlContext.createDataFrame(df1)
#dfs.registerTempTable('Locations')

In [ ]:
%sql
select * from Locations;

com.databricks.backend.common.rpc.DatabricksExceptions$SQLExecutionException: org.apache.spark.sql.AnalysisException: Table or view not found: Locations; line 1 pos 14
	at org.apache.spark.sql.catalyst.analysis.package$AnalysisErrorAt.failAnalysis(package.scala:47)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$.org$apache$spark$sql$catalyst$analysis$Analyzer$ResolveRelations$$lookupTableFromCatalog(Analyzer.scala:748)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$.resolveRelation(Analyzer.scala:693)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$$anonfun$apply$8.applyOrElse(Analyzer.scala:729)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$$anonfun$apply$8.applyOrElse(Analyzer.scala:722)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1$$anonfun$apply$1.apply(AnalysisHelper.scala:90)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1$$anonfun$apply$1.apply(AnalysisHelper.scala:90)
	at org.apache.spark.sql.catalyst.trees.CurrentOrigin$.withOrigin(TreeNode.scala:77)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1.apply(AnalysisHelper.scala:89)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1.apply(AnalysisHelper.scala:86)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$.allowInvokingTransformsInAnalyzer(AnalysisHelper.scala:194)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$class.resolveOperatorsUp(AnalysisHelper.scala:86)
	at org.apache.spark.sql.catalyst.plans.logical.LogicalPlan.resolveOperatorsUp(LogicalPlan.scala:29)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1$$anonfun$1.apply(AnalysisHelper.scala:87)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1$$anonfun$1.apply(AnalysisHelper.scala:87)
	at org.apache.spark.sql.catalyst.trees.TreeNode$$anonfun$8.apply(TreeNode.scala:354)
	at org.apache.spark.sql.catalyst.trees.TreeNode.mapProductIterator(TreeNode.scala:208)
	at org.apache.spark.sql.catalyst.trees.TreeNode.mapChildren(TreeNode.scala:352)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1.apply(AnalysisHelper.scala:87)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$$anonfun$resolveOperatorsUp$1.apply(AnalysisHelper.scala:86)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$.allowInvokingTransformsInAnalyzer(AnalysisHelper.scala:194)
	at org.apache.spark.sql.catalyst.plans.logical.AnalysisHelper$class.resolveOperatorsUp(AnalysisHelper.scala:86)
	at org.apache.spark.sql.catalyst.plans.logical.LogicalPlan.resolveOperatorsUp(LogicalPlan.scala:29)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$.apply(Analyzer.scala:722)
	at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$.apply(Analyzer.scala:662)
	at org.apache.spark.sql.catalyst.rules.RuleExecutor$$anonfun$execute$1$$anonfun$apply$1.apply(RuleExecutor.scala:112)
	at org.apache.spark.sql.catalyst.rules.RuleExecutor$$anonfun$execute$1$$anonfun$apply$1.apply(RuleExecutor.scala:109)
	at scala.collection.LinearSeqOptimized$class.foldLeft(LinearSeqOptimized.scala:124)
	at scala.collection.immutable.List.foldLeft(List.scala:84)
	at org.apache.spark.sql.catalyst.rules.RuleExecutor$$anonfun$execute$1.apply(RuleExecutor.scala:109)
	at org.apache.spark.sql.catalyst.rules.RuleExecutor$$anonfun$execute$1.apply(RuleExecutor.scala:101)
	at scala.collection.immutable.List.foreach(List.scala:392)
	at org.apache.spark.sql.catalyst.rules.RuleExecutor.execute(RuleExecutor.scala:101)
	at org.apache.spark.sql.catalyst.analysis.Analyzer.org$apache$spark$sql$catalyst$analysis$Analyzer$$executeSameContext(Analyzer.scala:136)
	at org.apache.spark.sql.catalyst.analysis.Analyzer.execute(Analyzer.scala:130)
	at o

In [ ]:
dfloc=spark.read.csv('/FileStore/tables/SupplyChainLocationsOutputNew.csv',header=True,inferSchema=True)

#/FileStore/tables/LocationSupplyChain.csv

In [ ]:
#dfloc.show()

In [ ]:
dfloc = dfloc.toPandas()
dfloc.drop('_c0',axis=1,inplace=True)

In [ ]:
#Joining with resolved location
SC_Merged_Local=SC_Merged_Local.merge(dfloc,on='Location',how='inner')
SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 FinalLoc 
 State 
 
 
 
 
 0 
 NaN 
 NaN 
 256878.4000 
 NaN 
 NaN 
 266363.3111 
 20 
 BLGC-V2 
 Atlanta, GA 
 3/1/2019 
 ... 
 NaN 
 NaN 
 450165.3333 
 NaN 
 NaN 
 517376.5727 
 20.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 1 
 192278.4091 
 209132.6667 
 222589.6667 
 278020.0000 
 302435.8334 
 238716.3648 
 32 
 ATTY-M1 
 Atlanta, GA 
 3/1/2019 
 ... 
 293156.000 
 319235.9133 
 421046.1400 
 558780.4250 
 867661.9184 
 471873.3017 
 32.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 2 
 127012.2500 
 158983.3334 
 184191.5034 
 221504.0000 
 259384.0820 
 186354.9924 
 85 
 ATTY-L4 
 Atlanta, GA 
 3/1/2019 
 ... 
 168421.375 
 209255.4762 
 247579.5800 
 296818.8600 
 508487.1135 
 268689.1704 
 85.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 3 
 117974.0000 
 134694.1249 
 153470.6667 
 176457.8332 
 195926.5000 
 155479.5208 
 60 
 ATTY-L3 
 Atlanta, GA 
 3/1/2019 
 ... 
 NaN 
 162072.5382 
 182371.6700 
 223140.0973 
 NaN 
 204355.2296 
 60.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 4 
 NaN 
 121333.5000 
 129406.0000 
 170833.3333 
 NaN 
 137985.9762 
 13 
 ATTY-L2 
 Atlanta, GA 
 3/1/2019 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 
 5 rows × 27 columns

In [ ]:
# aging
aging.head()

State 
 Region 
 ECIPercent 
 EffectiveDate 
 ObsoleteDate 
 
 
 
 
 0 
 Alaska 
 West 
 3.24% 
 2020-03-05 
 
 
 
 1 
 Arizona 
 West 
 3.24% 
 2020-03-05 
 
 
 
 2 
 California 
 West 
 3.24% 
 2020-03-05 
 
 
 
 3 
 Colorado 
 West 
 3.24% 
 2020-03-05 
 
 
 
 4 
 Hawaii 
 West 
 3.24% 
 2020-03-05

In [ ]:
SC_Merged_National['Survey Release Date'] =  pd.to_datetime(SC_Merged_National['Survey Release Date'])
SC_Merged_Local['Survey Release Date'] =  pd.to_datetime(SC_Merged_Local['Survey Release Date'])

In [ ]:
# Calculate aging days
SC_Merged_Local['Ageing_Days']=SC_Merged_Local['Survey Release Date'].apply(lambda x: (Ageing_date-x).days)
SC_Merged_National['Ageing_Days']=SC_Merged_National['Survey Release Date'].apply(lambda x: (Ageing_date-x).days)
#SC_Merged_Local['ECI Percent'] = ''

In [ ]:
# Get ECI percent for each state from aging column
SC_Merged_Local=SC_Merged_Local.merge(aging,on='State',how='inner')
SC_Merged_National=SC_Merged_National.merge(aging,left_on='Location',right_on='State',how='inner')
SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC Avg 
 TDC Emp 
 TableNbr 
 FinalLoc 
 State 
 Ageing_Days 
 Region 
 ECIPercent 
 EffectiveDate 
 ObsoleteDate 
 
 
 
 
 0 
 NaN 
 NaN 
 256878.4000 
 NaN 
 NaN 
 266363.3111 
 20 
 BLGC-V2 
 Atlanta, GA 
 2019-03-01 
 ... 
 517376.5727 
 20.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 458 
 Midwest 
 3.00% 
 2020-03-05 
 
 
 
 1 
 192278.4091 
 209132.6667 
 222589.6667 
 278020.0000 
 302435.8334 
 238716.3648 
 32 
 ATTY-M1 
 Atlanta, GA 
 2019-03-01 
 ... 
 471873.3017 
 32.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 458 
 Midwest 
 3.00% 
 2020-03-05 
 
 
 
 2 
 127012.2500 
 158983.3334 
 184191.5034 
 221504.0000 
 259384.0820 
 186354.9924 
 85 
 ATTY-L4 
 Atlanta, GA 
 2019-03-01 
 ... 
 268689.1704 
 85.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 458 
 Midwest 
 3.00% 
 2020-03-05 
 
 
 
 3 
 117974.0000 
 134694.1249 
 153470.6667 
 176457.8332 
 195926.5000 
 155479.5208 
 60 
 ATTY-L3 
 Atlanta, GA 
 2019-03-01 
 ... 
 204355.2296 
 60.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 458 
 Midwest 
 3.00% 
 2020-03-05 
 
 
 
 4 
 NaN 
 121333.5000 
 129406.0000 
 170833.3333 
 NaN 
 137985.9762 
 13 
 ATTY-L2 
 Atlanta, GA 
 2019-03-01 
 ... 
 NaN 
 NaN 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 458 
 Midwest 
 3.00% 
 2020-03-05 
 
 
 
 
 5 rows × 32 columns

In [ ]:
SC_Merged_Local.drop(['EffectiveDate','ObsoleteDate','Region'],axis=1,inplace=True)
SC_Merged_National.drop(['EffectiveDate','ObsoleteDate','Region'],axis=1,inplace=True)

In [ ]:
# convert ECI percent to float
SC_Merged_Local['ECIPercent'] = SC_Merged_Local['ECIPercent'].str.replace(r'%', '').astype('float') / 100.0
SC_Merged_National['ECIPercent'] = SC_Merged_National['ECIPercent'].str.replace(r'%', '').astype('float') / 100.0

# Aged ECI percent
SC_Merged_Local['Aged_ECI_Percent']=pow(1 + SC_Merged_Local['ECIPercent'],(SC_Merged_Local['Ageing_Days']/365))
SC_Merged_National['Aged_ECI_Percent']=pow(1 + SC_Merged_National['ECIPercent'],(SC_Merged_National['Ageing_Days']/365))

In [ ]:
# columns to age - This should come from mapping file
columns_to_be_aged = ['Base Avg', 'Base 90 p', 'Base 75 p','Base 50 p', 'Base 25 p', 'Base 10 p','TCC Avg', 'TCC 90 p', 'TCC 75 p','TCC 50 p', 'TCC 25 p', 'TCC 10 p','TDC Avg', 'TDC 90 p', 'TDC 75 p','TDC 50 p', 'TDC 25 p', 'TDC 10 p']

# Convert object to numeric
SC_Merged_Local[columns_to_be_aged] = SC_Merged_Local[columns_to_be_aged].apply(pd.to_numeric)
SC_Merged_National[columns_to_be_aged] = SC_Merged_National[columns_to_be_aged].apply(pd.to_numeric)

# Multiply with Aged_ECI_Percent
SC_Merged_Local[columns_to_be_aged].apply(lambda x:x*SC_Merged_Local['Aged_ECI_Percent'])
SC_Merged_National[columns_to_be_aged].apply(lambda x:x*SC_Merged_National['Aged_ECI_Percent'])

# after aging remove columns
SC_Merged_Local.drop(['Ageing_Days', 'ECIPercent', 'Aged_ECI_Percent'], axis = 1, inplace = True )
SC_Merged_National.drop(['Ageing_Days', 'ECIPercent', 'Aged_ECI_Percent'], axis = 1, inplace = True )
SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC 10 p 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 FinalLoc 
 State 
 
 
 
 
 0 
 NaN 
 NaN 
 256878.4000 
 NaN 
 NaN 
 266363.3111 
 20 
 BLGC-V2 
 Atlanta, GA 
 2019-03-01 
 ... 
 NaN 
 NaN 
 450165.3333 
 NaN 
 NaN 
 517376.5727 
 20.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 1 
 192278.4091 
 209132.6667 
 222589.6667 
 278020.0000 
 302435.8334 
 238716.3648 
 32 
 ATTY-M1 
 Atlanta, GA 
 2019-03-01 
 ... 
 293156.000 
 319235.9133 
 421046.1400 
 558780.4250 
 867661.9184 
 471873.3017 
 32.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 2 
 127012.2500 
 158983.3334 
 184191.5034 
 221504.0000 
 259384.0820 
 186354.9924 
 85 
 ATTY-L4 
 Atlanta, GA 
 2019-03-01 
 ... 
 168421.375 
 209255.4762 
 247579.5800 
 296818.8600 
 508487.1135 
 268689.1704 
 85.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 3 
 117974.0000 
 134694.1249 
 153470.6667 
 176457.8332 
 195926.5000 
 155479.5208 
 60 
 ATTY-L3 
 Atlanta, GA 
 2019-03-01 
 ... 
 NaN 
 162072.5382 
 182371.6700 
 223140.0973 
 NaN 
 204355.2296 
 60.0 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 4 
 NaN 
 121333.5000 
 129406.0000 
 170833.3333 
 NaN 
 137985.9762 
 13 
 ATTY-L2 
 Atlanta, GA 
 2019-03-01 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 7 
 Northeast Lower Peninsula of Michigan nonmetro... 
 Michigan 
 
 
 
 5 rows × 27 columns

In [ ]:
#Moving files from DBFS to ADLS
#Supply Chain Job Mapping file
#dbutils.fs.mv('/FileStore/tables/Supply_Chain_Job_Mapping.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

In [ ]:
#Taking the required columns
SC_Job_Mapping = SC_Job_Mapping[['Job Code','Empsight Job code','Western Mgmt Job code','KFHG Job Code','Mercer Job code']]

#Renaming the columns
SC_Job_Mapping = SC_Job_Mapping.rename(columns = {'Job Code':'WMT Job Code','Empsight Job code':'empsight','Western Mgmt Job code':'wmg',
                                                 'KFHG Job Code':'kornferry','Mercer Job code':'mercer'})

SC_Job_Mapping=pd.melt(SC_Job_Mapping,id_vars=["WMT Job Code"],var_name="Survey Name",value_name="Job Code")
SC_Job_Mapping.head()

WMT Job Code 
 Survey Name 
 Job Code 
 
 
 
 
 0 
 100021011 
 empsight 
 SCLG-D2 
 
 
 1 
 3737 
 empsight 
 None 
 
 
 2 
 None 
 empsight 
 None 
 
 
 3 
 expense 
 empsight 
 None 
 
 
 4 
 None 
 empsight 
 None

In [ ]:
#Reading files from ADLS into dataframe
#Supply Chain Job Mapping
SC_Job_Mapping = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Supply_Chain_Job_Mapping.csv")

SC_Job_Mapping = SC_Job_Mapping.toPandas()

#Filtering only the SC job codes
#SC_Job_Mapping = SC_Job_Mapping[SC_Job_Mapping['Tech or SC Surveys']=='SC']
SC_Job_Mapping.head()

JAID 
 Job Code 
 Job Title 
 Count of WIN 
 Job level 
 Tech or SC Surveys 
 Job Family Group 
 Job Family 
 Priority 
 Empsight Job code 
 ... 
 Culpepper Job code 
 Culpepper Job Title 
 Culpepper Job Description 
 IPAS Job code 
 IPAS Job Title 
 IPAS Job Description 
 Radford Job Code 
 Radford Job Title 
 Radford Job Description 
 Remarks 
 
 
 
 
 0 
 LOGF12626 
 100021011 
 SENIOR OPERATIONS DIRECTOR II, FULFILLMENT CEN... 
 6 
 9 
 SC 
 Global_JFG_Supply_Chain 
 Global_JF_Warehouse_Management 
 FC - 1 
 SCLG-D2 
 ... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 
 
 1 
 Distribution Center Regional Manager: Responsi... 
 3737 
 District Manager VII 
 District Manager VII (3737)\n 
 None 
 None 
 None 
 None 
 None 
 None 
 ... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 
 
 2 
 General Characteristics 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 ... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 
 
 3 
 Accountable for the overall management of a gr... 
 expense 
 and profit objectives; areas of responsibilit... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 ... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 
 
 4 
 Representative Activities 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 ... 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 None 
 
 
 
 5 rows × 31 columns

In [ ]:
#Renaming the columns
ref_tables=ref_tables.rename(columns={'table_nbr':'TableNbr','survey_name':'Survey Name'})
ref_tables.head()

TableNbr 
 Survey Name 
 
 
 
 
 0 
 5 
 kornferry_national 
 
 
 1 
 12 
 culpepper_national 
 
 
 2 
 8 
 empsight_national 
 
 
 3 
 6 
 mercer_national 
 
 
 4 
 10 
 wmg_national

In [ ]:
#Joining the merged local and national data with job mapping file to get the respective Walmart job code
SC_Merged_Local=(SC_Merged_Local.merge(ref_tables,on = 'TableNbr',how='inner')).merge(SC_Job_Mapping,on=['Survey Name','Job Code'],how='inner')

SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 FinalLoc 
 State 
 Survey Name 
 WMT Job Code 
 
 
 
 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100012538 
 
 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100012539 
 
 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100017203 
 
 
 3 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100019133 
 
 
 4 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100021012 
 
 
 
 5 rows × 29 columns

In [ ]:
SC_Merged_National=SC_Merged_National.merge(ref_tables,on='TableNbr',how='inner')

SC_Merged_National['Survey Name']=SC_Merged_National['Survey Name'].str.split('_').str[0]

SC_Merged_National=SC_Merged_National.merge(SC_Job_Mapping,on=['Survey Name','Job Code'],how='inner')
SC_Merged_National.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC 25 p 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 State 
 Survey Name 
 WMT Job Code 
 
 
 
 
 0 
 143517.6480 
 159134.5000 
 170000.0000 
 185927.2200 
 221992.0640 
 176203.2756 
 27 
 BSDV-D1 
 National 
 2019-03-01 
 ... 
 187918.6050 
 232500.0000 
 275352.9020 
 325328.3100 
 243027.1080 
 27.0 
 8 
 National 
 empsight 
 100017091 
 
 
 1 
 82115.4390 
 106142.4250 
 138503.0400 
 165294.6800 
 180084.4500 
 135288.9299 
 82 
 BSDV-M1 
 National 
 2019-03-01 
 ... 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 8 
 National 
 empsight 
 100017088 
 
 
 2 
 174272.0618 
 201530.8059 
 218216.5059 
 235556.2420 
 243990.4444 
 216179.7367 
 52 
 SCMG-D2 
 National 
 2019-03-01 
 ... 
 240155.1029 
 307081.4400 
 377464.2644 
 432830.6668 
 313260.0312 
 52.0 
 8 
 National 
 empsight 
 100019133 
 
 
 3 
 129842.5000 
 147264.2500 
 175651.8400 
 196495.6625 
 216911.2000 
 174905.9138 
 97 
 SCMG-D1 
 National 
 2019-03-01 
 ... 
 174848.2500 
 222658.0221 
 297634.0200 
 346413.2380 
 243521.7619 
 97.0 
 8 
 National 
 empsight 
 100019128 
 
 
 4 
 108616.4950 
 124604.5433 
 150039.7500 
 182608.5300 
 200636.4700 
 152830.3116 
 133 
 SCMG-M2 
 National 
 2019-03-01 
 ... 
 145057.3458 
 175994.2583 
 254838.9045 
 311124.0812 
 198536.3681 
 133.0 
 8 
 National 
 empsight 
 100019119 
 
 
 
 5 rows × 28 columns

In [ ]:
col_names_local=SC_Merged_Local.columns
col_names_national=SC_Merged_National.columns

if any('TCC' in c for c in col_names_local) & any('TDC' in c for c in col_names_local):
    parameter_local='both'
elif any('TDC' in c for c in col_names_local):
    parameter_local='TDC'
elif any('TCC' in c for c in col_names_local):
    parameter_local='TCC'
else:
  parameter_local='None'

if any('TCC' in c for c in col_names_national) & any('TDC' in c for c in col_names_national):
    parameter_national='both'
elif any('TDC' in c for c in col_names_national):
    parameter_national='TDC'
elif any('TCC' in c for c in col_names_national):
    parameter_national='TCC'
else:
  parameter_national='None'

SC_Merged_Local=levelling(SC_Merged_Local,parameter_local)
SC_Merged_National=levelling(SC_Merged_National,parameter_national)

SC_Merged_Local.head()

Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 Job Code 
 Location 
 Survey Release Date 
 ... 
 TDC 50 p 
 TDC 75 p 
 TDC 90 p 
 TDC Avg 
 TDC Emp 
 TableNbr 
 FinalLoc 
 State 
 Survey Name 
 WMT Job Code 
 
 
 
 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 0 
 0 
 0 
 0 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100012538 
 
 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 0 
 0 
 0 
 0 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100012539 
 
 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 0 
 0 
 0 
 0 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100017203 
 
 
 3 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 0 
 0 
 0 
 0 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100019133 
 
 
 4 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 DCM-M3 
 Detroit,MI 
 2019-08-11 
 ... 
 0 
 0 
 0 
 0 
 NaN 
 9 
 Detroit-Warren-Dearborn, MI 
 Michigan 
 wmg 
 100021012 
 
 
 
 5 rows × 29 columns

In [ ]:
SC_Merged_National['FinalLoc']="National"

In [ ]:
# creating final table with 
SC_Merged_final=SC_Merged_Local.append(SC_Merged_National, ignore_index=True)

In [ ]:
#SC_Merged_final = SC_Merged_final.toPandas()

In [ ]:
# WEIGHT CALCULATION: 

# Take column names from mapping 

weig_df = pd.DataFrame(columns = ['Base Emp Count','1_Base 90 p Wt' ,'1_Base 75 p Wt','1_Base Avg Wt','1_Base 50 p Wt','1_Base 25 p Wt','1_Base 10 p Wt','Base 90 p Wt','Base 75 p Wt','Base Avg Wt','Base 50 p Wt','Base 25 p Wt','Base 10 p Wt',
                                  'TCC Emp Count','1_TCC 90 p Wt' ,'1_TCC 75 p Wt','1_TCC Avg Wt','1_TCC 50 p Wt','1_TCC 25 p Wt','1_TCC 10 p Wt','TCC 90 p Wt','TCC 75 p Wt','TCC Avg Wt','TCC 50 p Wt','TCC 25 p Wt','TCC 10 p Wt',
                                  'TDC Emp Count','1_TDC 90 p Wt' ,'1_TDC 75 p Wt','1_TDC Avg Wt','1_TDC 50 p Wt','1_TDC 25 p Wt','1_TDC 10 p Wt','TDC 90 p Wt','TDC 75 p Wt','TDC Avg Wt','TDC 50 p Wt','TDC 25 p Wt','TDC 10 p Wt'])

#Base
weig_df['Base Emp Count']  = SC_Merged_final['Base Emp']
weig_df['1_Base 90 p Wt'] = weig_df['Base Emp Count'] * 0.9 + 1
weig_df['1_Base 75 p Wt'] = weig_df['Base Emp Count'] * 0.75 + 1
weig_df['1_Base Avg Wt'] = weig_df['Base Emp Count'] * 0.5 + 1
weig_df['1_Base 50 p Wt'] = weig_df['Base Emp Count'] * 0.5 + 1
weig_df['1_Base 25 p Wt'] = weig_df['Base Emp Count'] * 0.25 + 1
weig_df['1_Base 10 p Wt'] = weig_df['Base Emp Count'] * 0.1 + 1

weig_df['Base 90 p Wt'] = weig_df['Base Emp Count'] - weig_df['1_Base 90 p Wt'] 
weig_df['Base 75 p Wt'] = weig_df['1_Base 90 p Wt'] - weig_df['1_Base 75 p Wt']
weig_df['Base Avg Wt'] = weig_df['1_Base 75 p Wt'] - weig_df['1_Base Avg Wt']
weig_df['Base 50 p Wt'] = weig_df['1_Base 75 p Wt'] - weig_df['1_Base 50 p Wt']
weig_df['Base 25 p Wt'] = weig_df['1_Base 50 p Wt'] - weig_df['1_Base 25 p Wt']
weig_df['Base 10 p Wt'] = weig_df['1_Base 25 p Wt'] - weig_df['1_Base 10 p Wt']

#TCC
weig_df['TCC Emp Count']  = SC_Merged_final['TCC Emp']
weig_df['1_TCC 90 p Wt'] = weig_df['TCC Emp Count'] * 0.9 + 1
weig_df['1_TCC 75 p Wt'] = weig_df['TCC Emp Count'] * 0.75 + 1
weig_df['1_TCC Avg Wt'] = weig_df['TCC Emp Count'] * 0.5 + 1
weig_df['1_TCC 50 p Wt'] = weig_df['TCC Emp Count'] * 0.5 + 1
weig_df['1_TCC 25 p Wt'] = weig_df['TCC Emp Count'] * 0.25 + 1
weig_df['1_TCC 10 p Wt'] = weig_df['TCC Emp Count'] * 0.1 + 1

weig_df['TCC 90 p Wt'] = weig_df['TCC Emp Count'] - weig_df['1_TCC 90 p Wt'] 
weig_df['TCC 75 p Wt'] = weig_df['1_TCC 90 p Wt'] - weig_df['1_TCC 75 p Wt']
weig_df['TCC Avg Wt'] = weig_df['1_TCC 75 p Wt'] - weig_df['1_TCC Avg Wt']
weig_df['TCC 50 p Wt'] = weig_df['1_TCC 75 p Wt'] - weig_df['1_TCC 50 p Wt']
weig_df['TCC 25 p Wt'] = weig_df['1_TCC 50 p Wt'] - weig_df['1_TCC 25 p Wt']
weig_df['TCC 10 p Wt'] = weig_df['1_TCC 25 p Wt'] - weig_df['1_TCC 10 p Wt']

#TDC
weig_df['TDC Emp Count']  = SC_Merged_final['TDC Emp']
weig_df['1_TDC 90 p Wt'] = weig_df['TDC Emp Count'] * 0.9 + 1
weig_df['1_TDC 75 p Wt'] = weig_df['TDC Emp Count'] * 0.75 + 1
weig_df['1_TDC Avg Wt'] = weig_df['TDC Emp Count'] * 0.5 + 1
weig_df['1_TDC 50 p Wt'] = weig_df['TDC Emp Count'] * 0.5 + 1
weig_df['1_TDC 25 p Wt'] = weig_df['TDC Emp Count'] * 0.25 + 1
weig_df['1_TDC 10 p Wt'] = weig_df['TDC Emp Count'] * 0.1 + 1

weig_df['TDC 90 p Wt'] = weig_df['TDC Emp Count'] - weig_df['1_TDC 90 p Wt'] 
weig_df['TDC 75 p Wt'] = weig_df['1_TDC 90 p Wt'] - weig_df['1_TDC 75 p Wt']
weig_df['TDC Avg Wt'] = weig_df['1_TDC 75 p Wt'] - weig_df['1_TDC Avg Wt']
weig_df['TDC 50 p Wt'] = weig_df['1_TDC 75 p Wt'] - weig_df['1_TDC 50 p Wt']
weig_df['TDC 25 p Wt'] = weig_df['1_TDC 50 p Wt'] - weig_df['1_TDC 25 p Wt']
weig_df['TDC 10 p Wt'] = weig_df['1_TDC 25 p Wt'] - weig_df['1_TDC 10 p Wt']

weig_df = weig_df[['Base 90 p Wt','Base 75 p Wt' , 'Base Avg Wt' , 'Base 50 p Wt' , 'Base 25 p Wt' , 'Base 10 p Wt',
                   'TCC 90 p Wt','TCC 75 p Wt' , 'TCC Avg Wt' , 'TCC 50 p Wt' , 'TCC 25 p Wt' , 'TCC 10 p Wt',
                   'TDC 90 p Wt','TDC 75 p Wt' , 'TDC Avg Wt' , 'TDC 50 p Wt' , 'TDC 25 p Wt' , 'TDC 10 p Wt' ]]

# remove all negatives
weig_df = weig_df.mask(weig_df < 0, 0)

#Filling NA with 0
weig_df=weig_df.fillna(0)
# Round all weights and convert it to integer
weig_df.round(decimals=0)
weig_df = weig_df.astype(int)
weig_df

weig_df.head()

Base 90 p Wt 
 Base 75 p Wt 
 Base Avg Wt 
 Base 50 p Wt 
 Base 25 p Wt 
 Base 10 p Wt 
 TCC 90 p Wt 
 TCC 75 p Wt 
 TCC Avg Wt 
 TCC 50 p Wt 
 TCC 25 p Wt 
 TCC 10 p Wt 
 TDC 90 p Wt 
 TDC 75 p Wt 
 TDC Avg Wt 
 TDC 50 p Wt 
 TDC 25 p Wt 
 TDC 10 p Wt 
 
 
 
 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 1 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 2 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 3 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 4 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0

In [ ]:
# Join out_df and weight calculation
input_df = pd.concat([SC_Merged_final, weig_df], axis=1)
input_df.columns

Out[ 52 ]: Index(['Base 10 p', 'Base 25 p', 'Base 50 p', 'Base 75 p', 'Base 90 p',
 'Base Avg', 'Base Emp', 'FinalLoc', 'Job Code', 'Location', 'State',
 'Survey Name', 'Survey Release Date', 'TCC 10 p', 'TCC 25 p',
 'TCC 50 p', 'TCC 75 p', 'TCC 90 p', 'TCC Avg', 'TCC Emp', 'TDC 10 p',
 'TDC 25 p', 'TDC 50 p', 'TDC 75 p', 'TDC 90 p', 'TDC Avg', 'TDC Emp',
 'TableNbr', 'WMT Job Code', 'Base 90 p Wt', 'Base 75 p Wt',
 'Base Avg Wt', 'Base 50 p Wt', 'Base 25 p Wt', 'Base 10 p Wt',
 'TCC 90 p Wt', 'TCC 75 p Wt', 'TCC Avg Wt', 'TCC 50 p Wt',
 'TCC 25 p Wt', 'TCC 10 p Wt', 'TDC 90 p Wt', 'TDC 75 p Wt',
 'TDC Avg Wt', 'TDC 50 p Wt', 'TDC 25 p Wt', 'TDC 10 p Wt'],
 dtype='object')

In [ ]:
# convert all columns to float - columns from mapping
input_df[['Base Avg', 'Base 90 p','Base 75 p', 'Base 50 p', 'Base 25 p', 'Base 10 p', 'Base Emp','Base 90 p Wt','Base 75 p Wt' , 'Base Avg Wt' , 'Base 50 p Wt' , 'Base 25 p Wt' , 'Base 10 p Wt',
         'TCC Avg', 'TCC 90 p','TCC 75 p', 'TCC 50 p', 'TCC 25 p', 'TCC 10 p', 'TCC Emp','TCC 90 p Wt','TCC 75 p Wt' , 'TCC Avg Wt' , 'TCC 50 p Wt' , 'TCC 25 p Wt' , 'TCC 10 p Wt',
         'TDC Avg', 'TDC 90 p','TDC 75 p', 'TDC 50 p', 'TDC 25 p', 'TDC 10 p', 'TDC Emp','TDC 90 p Wt','TDC 75 p Wt' , 'TDC Avg Wt' , 'TDC 50 p Wt' , 'TDC 25 p Wt' , 'TDC 10 p Wt']] = input_df[['Base Avg', 'Base 90 p','Base 75 p', 'Base 50 p', 'Base 25 p', 'Base 10 p', 'Base Emp','Base 90 p Wt','Base 75 p Wt' , 'Base Avg Wt' , 'Base 50 p Wt' , 'Base 25 p Wt' , 'Base 10 p Wt',
         'TCC Avg', 'TCC 90 p','TCC 75 p', 'TCC 50 p', 'TCC 25 p', 'TCC 10 p', 'TCC Emp','TCC 90 p Wt','TCC 75 p Wt' , 'TCC Avg Wt' , 'TCC 50 p Wt' , 'TCC 25 p Wt' , 'TCC 10 p Wt',
         'TDC Avg', 'TDC 90 p','TDC 75 p', 'TDC 50 p', 'TDC 25 p', 'TDC 10 p', 'TDC Emp','TDC 90 p Wt','TDC 75 p Wt' , 'TDC Avg Wt' , 'TDC 50 p Wt' , 'TDC 25 p Wt' , 'TDC 10 p Wt']].apply(pd.to_numeric)

input_df.head()


Base 10 p 
 Base 25 p 
 Base 50 p 
 Base 75 p 
 Base 90 p 
 Base Avg 
 Base Emp 
 FinalLoc 
 Job Code 
 Location 
 ... 
 TCC Avg Wt 
 TCC 50 p Wt 
 TCC 25 p Wt 
 TCC 10 p Wt 
 TDC 90 p Wt 
 TDC 75 p Wt 
 TDC Avg Wt 
 TDC 50 p Wt 
 TDC 25 p Wt 
 TDC 10 p Wt 
 
 
 
 
 0 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 Detroit-Warren-Dearborn, MI 
 DCM-M3 
 Detroit,MI 
 ... 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 1 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 Detroit-Warren-Dearborn, MI 
 DCM-M3 
 Detroit,MI 
 ... 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 2 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 Detroit-Warren-Dearborn, MI 
 DCM-M3 
 Detroit,MI 
 ... 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 3 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 Detroit-Warren-Dearborn, MI 
 DCM-M3 
 Detroit,MI 
 ... 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 4 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 5 
 Detroit-Warren-Dearborn, MI 
 DCM-M3 
 Detroit,MI 
 ... 
 1 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 
 5 rows × 47 columns

In [ ]:
# rename column names to match bootstrapping code
input_df.rename(columns = {'FinalLoc':'Locations' , 'WMT Job Code':'Company Job Code'}, inplace = True) 

In [ ]:
#input_df.fillna(0)

In [ ]:
#Creating df Dataframe which will be input for Bootstrapping code
df = input_df.copy()
df=df.fillna(0)

In [ ]:
df.dtypes

Out[ 57 ]: Base 10 p float64
Base 25 p float64
Base 50 p float64
Base 75 p float64
Base 90 p float64
Base Avg float64
Base Emp int32
Locations object
Job Code object
Location object
State object
Survey Name object
Survey Release Date datetime64[ns]
TCC 10 p float64
TCC 25 p float64
TCC 50 p float64
TCC 75 p float64
TCC 90 p float64
TCC Avg float64
TCC Emp float64
TDC 10 p float64
TDC 25 p float64
TDC 50 p float64
TDC 75 p float64
TDC 90 p float64
TDC Avg float64
TDC Emp float64
TableNbr int64
Company Job Code object
Base 90 p Wt int64
Base 75 p Wt int64
Base Avg Wt int64
Base 50 p Wt int64
Base 25 p Wt int64
Base 10 p Wt int64
TCC 90 p Wt int64
TCC 75 p Wt int64
TCC Avg Wt int64
TCC 50 p Wt int64
TCC 25 p Wt int64
TCC 10 p Wt int64
TDC 90 p Wt int64
TDC 75 p Wt int64
TDC Avg Wt int64
TDC 50 p Wt int64
TDC 25 p Wt int64
TDC 10 p Wt int64
dtype: object

In [ ]:
#BootStrapping Code
def salary_calculation(df, sal): 
    
    if sal + ' 10 p' in df.columns:
        np_sal = np.array(df[[sal + ' 10 p']].values)
    if sal + ' 25 p' in df.columns:  
        np_sal=np.append(np_sal,df[[sal +' 25 p']].values)
    if sal + ' 50 p' in df.columns:
        np_sal=np.append(np_sal,df[[sal+' 50 p']].values)
    if sal + ' 60 p' in df.columns:
        np_sal=np.append(np_sal,df[[sal+' 60 p']].values)
    if sal + ' 75 p' in df.columns:
        np_sal=np.append(np_sal,df[[sal+' 75 p']].values)
    if sal + ' 90 p' in df.columns:     
        np_sal=np.append(np_sal,df[[sal+' 90 p']].values)
    if sal + ' Avg' in df.columns:      
        np_sal=np.append(np_sal,df[[sal+' Avg']].values)
    
    return np_sal

# Salary weights
def sweights_calculation(df, sal): 
    if sal +' 10 p Wt' in df.columns:
        #print(' 10 p Wt')
        np_Wt = np.array(df[[sal +' 10 p Wt']].values) 
    if sal +' 25 p Wt' in df.columns:
        #print(' 25 p Wt')
        np_Wt=np.append(np_Wt,df[[sal +' 25 p Wt']].values)      
    if sal +' 50 p Wt' in df.columns:    
        #print(' 50 p Wt')
        np_Wt=np.append(np_Wt,df[[sal +' 50 p Wt']].values)
    if sal +' 60 p Wt' in df.columns: 
        #print(' 60 p Wt') 
        np_Wt=np.append(np_Wt,df[[sal +' 60 p Wt']].values)        
    if sal +' 75 p Wt' in df.columns:
        #print(' 75 p Wt')
        np_Wt=np.append(np_Wt,df[[sal +' 75 p Wt']].values)
    if sal +' 90 p Wt' in df.columns:    
        #print(' 90 p Wt') 
        np_Wt=np.append(np_Wt,df[[sal +' 90 p Wt']].values)
    if sal +' Avg Wt' in df.columns: 
        #print(' Avg p Wt') 
        np_Wt=np.append(np_Wt,df[[sal +' Avg Wt']].values)      
    
    return np_Wt

import pandas as pd
import numpy as np
from pyspark.sql.types import *
from pyspark.sql.functions import col, count, rand, collect_list, explode, struct, count, lit
from pyspark.sql.functions import pandas_udf, PandasUDFType
from pyspark.sql.functions import lit

outdf=pd.DataFrame(columns=["ConfidenceInterval","Percentile",'low','mid','high','Salary','locjobcode'])
outdf['ConfidenceInterval'] = outdf['ConfidenceInterval'].astype('double')
outdf['Percentile'] = outdf['Percentile'].astype('double')
#outdf['factor'] = outdf['factor'].astype('double')
outdf['low'] = outdf['low'].astype('double')
outdf['mid'] = outdf['mid'].astype('double')
outdf['high'] = outdf['high'].astype('double')
outdf['Salary'] = outdf['Salary'].astype('object')
outdf['locjobcode'] = outdf['locjobcode'].astype('object')
outdf.loc[0] = [0.95,0.95,0.95,0.95,0.95,'a','a']
sparkdf = spark.createDataFrame(outdf)
jobschema = sparkdf.schema


outdf=pd.DataFrame(columns=["ConfidenceInterval","Percentile",'low','mid','high','Location','Company Job Code','Salary'])
outdf['ConfidenceInterval'] = outdf['ConfidenceInterval'].astype('double')
outdf['Percentile'] = outdf['Percentile'].astype('double')
outdf['low'] = outdf['low'].astype('double')
outdf['mid'] = outdf['mid'].astype('double')
outdf['high'] = outdf['high'].astype('double')
outdf['Location'] = outdf['Location'].astype('object')
outdf['Company Job Code'] = outdf['Company Job Code'].astype('object')
outdf['Salary'] = outdf['Salary'].astype('object')
outdf.loc[0] = [0.95,0.95,0.95,0.95,0.95,'a','a','a']
sparkdf = spark.createDataFrame(outdf)
overalljobschema = sparkdf.schema

df['groupcol'] = df['Locations'] +"|"+df['Company Job Code']
groupcolumn = "groupcol"

@pandas_udf(jobschema, PandasUDFType.GROUPED_MAP)
def bootstrap_results(df):
    outdf=pd.DataFrame(columns=["ConfidenceInterval","Percentile",'low','mid','high','Salary','locjobcode'])
    group_key = df[groupcolumn].iloc[0]
    # construct the simulated sampling distribution
    for sal in ['Base','TCC','TDC']: 
        ## get the data for Sal calculation
        df_Sal_Wt= df.filter(regex=sal)
        df_Sal_Wt=df_Sal_Wt.copy()
        df_Sal_Wt[df_Sal_Wt <0]=0
        np_sal= salary_calculation(df_Sal_Wt,sal)
        
        ## get the Weights 
        np_Wt=sweights_calculation(df_Sal_Wt, sal)
        #print(np_sal)

        np_sal=np.repeat(np_sal, np_Wt)
        np_sal = np_sal[np.where(np_sal>0)]
        if(np_sal.size==0):
          outdf = outdf.append({"ConfidenceInterval":0.95,"Percentile":-1 ,'low': -1,'mid':-1,'high':-1,'Salary':'NA','locjobcode':'NA'}, ignore_index=True)   
          continue   
        for i in (10,25,50,75,90):
            sample_props = []
            for _ in range(10000):
                sample = np.random.choice(np_sal, size=100)
                sample_props.append(np.percentile(sample,i))

            sample_props=np.sort(sample_props)
            n=len(sample_props)
            p=0.95
            #for p in (0.8,0.85,0.9,0.95):
            u_pval = (1+p)/2.
            l_pval = (1-u_pval)
            l_indx = int(np.floor(n*l_pval))
            u_indx = int(np.floor(n*u_pval))
            outdf = outdf.append({"ConfidenceInterval":p,"Percentile":i,'low': sample_props[l_indx],'mid':(sample_props[l_indx]+sample_props[u_indx])/2,'high':sample_props[u_indx], 'Salary':sal, 'locjobcode':group_key}, ignore_index=True)  
    return outdf
  
df = spark.createDataFrame(df)
dfFinal = df.groupby(groupcolumn).apply(bootstrap_results)

from pyspark.sql.functions import split
from pyspark.sql.functions import lit
split_col = split(lit(dfFinal['locjobcode']), '\|')
dfFinal = dfFinal.withColumn('Location', split_col.getItem(0))
dfFinal = dfFinal.withColumn('JobCode', split_col.getItem(1))
dfFinal = dfFinal.drop('locjobcode')

In [ ]:
#Converting Output Dataframe from long to wide format and removing empty rows
dfFinal=dfFinal.filter(dfFinal.Percentile !='-1.0')

dfFinal=dfFinal.toPandas()

dfFinal =dfFinal.drop(['ConfidenceInterval'], axis=1)

df1=dfFinal.set_index(['JobCode','Location','Percentile','Salary']).unstack(['Salary','Percentile'])
df1 =df1.reset_index()

df1.columns=[y+"_"+x+"_"+str(z)  for x,y,z in df1.columns]

df1=df1.rename(columns={'_JobCode_': 'JobCode', '_Location_': 'Location'})

df1 = df1.set_index('JobCode').reset_index()

df1 = df1.set_index('Location').reset_index()


--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 <command-2305980921626467> in <module> () 
 2 dfFinal = dfFinal . filter ( dfFinal . Percentile != '-1.0' ) 
 3 
 ----> 4 dfFinal = dfFinal . toPandas ( ) 
 5 
 6 

 /databricks/spark/python/pyspark/sql/dataframe.py in toPandas (self) 
 2189 
 2190 # Below is toPandas without Arrow optimization. 
 -> 2191 pdf = pd . DataFrame . from_records ( self . collect ( ) , columns = self . columns ) 
 2192 
 2193 dtype = { } 

 /databricks/spark/python/pyspark/sql/dataframe.py in collect (self) 
 537 import pwd # Do this lazily since it's available on Linux only 
 538 username = pwd . getpwuid ( os . getuid ( ) ) . pw_name 
 --> 539 filename = self . _jdf . collectToPythonFile ( username ) 
 540 try : 
 541 serializer = BatchedSerializer ( PickleSerializer ( ) ) 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1255 answer = self . gateway_client . send_command ( command ) 
 1256 return_value = get_return_value(
 -> 1257 answer, self.gateway_client, self.target_id, self.name)
 1258 
 1259 for temp_arg in temp_args : 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 61 def deco ( * a , ** kw ) : 
 62 try : 
 ---> 63 return f ( * a , ** kw ) 
 64 except py4j . protocol . Py4JJavaError as e : 
 65 s = e . java_exception . toString ( ) 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 326 raise Py4JJavaError(
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 --> 328 format(target_id, ".", name), value)
 329 else : 
 330 raise Py4JError(

 Py4JJavaError : An error occurred while calling o2044.collectToPythonFile.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 160 in stage 66.0 failed 4 times, most recent failure: Lost task 160.3 in stage 66.0 (TID 976, 10.139.64.9, executor 9): java.net.SocketException: Broken pipe (Write failed)
	at java.net.SocketOutputStream.socketWrite0(Native Method)
	at java.net.SocketOutputStream.socketWrite(SocketOutputStream.java:111)
	at java.net.SocketOutputStream.write(SocketOutputStream.java:155)
	at java.io.BufferedOutputStream.flushBuffer(BufferedOutputStream.java:82)
	at java.io.BufferedOutputStream.flush(BufferedOutputStream.java:140)
	at java.io.DataOutputStream.flush(DataOutputStream.java:123)
	at org.apache.spark.api.python.BasePythonRunner$WriterThread$$anonfun$run$1.apply(PythonRunner.scala:400)
	at org.apache.spark.util.Utils$.logUncaughtExceptions(Utils.scala:2121)
	at org.apache.spark.api.python.BasePythonRunner$WriterThread.run(PythonRunner.scala:229)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.org$apache$spark$scheduler$DAGScheduler$$failJobAndIndependentStages(DAGScheduler.scala:2355)
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$abortStage$1.apply(DAGScheduler.scala:2343)
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$abortStage$1.apply(DAGScheduler.scala:2342)
	at scala.collection.mutable.ResizableArray$class.foreach(ResizableArray.scala:59)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:48)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2342)
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$handleTaskSetFailed$1.apply(DAGScheduler.scala:1096)
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$handleTaskSetFailed$1.apply(DAGScheduler.scala:1096)
	at scala.Option.foreach(Option.scala:257)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1096)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:2574)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:2522)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:2510)
	at org.apache.spark.util.EventLoop$$anon$1.run

In [ ]:
#Separating Local and National Blended Data

dfFinalLocal=df1[df1['Location']!='National']
dfFinalNational=df1[df1['Location']=='National']

In [ ]:
dfFinalLocal=dfFinalLocal.fillna(0)
dfFinalNational=dfFinalNational.fillna(0)

In [ ]:
#Local
if any('TCC' in c for c in dfFinalLocal.columns) & any('TDC' in c for c in dfFinalLocal.columns):
    parameter_local='both'
elif any('TDC' in c for c in dfFinalLocal.columns):
    parameter_local='TDC'
elif any('TCC' in c for c in dfFinalLocal.columns):
    parameter_local='TCC'
else:
  parameter_local='None'

dfFinalLocal=recalculate(dfFinalLocal,parameter_local,ranges)

#National
if any('TCC' in c for c in dfFinalNational.columns) & any('TDC' in c for c in dfFinalNational.columns):
    parameter_national='both'
elif any('TDC' in c for c in dfFinalNational.columns):
    parameter_national='TDC'
elif any('TCC' in c for c in dfFinalNational.columns):
    parameter_national='TCC'
else:
  parameter_national='None'

dfFinalNational=recalculate(dfFinalNational,parameter_national,ranges)


In [ ]:
#Renaming the comp components in national data
dfFinalNational.columns=dfFinalNational.columns.map(lambda x: x + '_n' if x!='JobCode' and  x!='Location' else x)

#Merging the national data with local data to impute
dfFinalLocal=dfFinalLocal.merge(dfFinalNational.loc[:,dfFinalNational.columns != 'Location'],on='JobCode',how='inner')

In [ ]:
#Imputation
if any('TCC' in c for c in dfFinalLocal.columns) & any('TDC' in c for c in dfFinalLocal.columns):
    parameter_local='both'
elif any('TDC' in c for c in dfFinalLocal.columns):
    parameter_local='TDC'
elif any('TCC' in c for c in dfFinalLocal.columns):
    parameter_local='TCC'
else:
  parameter_local='None'

dfFinalLocal=imputation(dfFinalLocal,parameter_local,ranges)

In [ ]:
#Creating copies for future use
cols_drop = [col for col in dfFinalLocal.columns if '_n' in col]
dfFinalLocal1=dfFinalLocal.drop(cols_drop,axis=1)

#dfFinalLocal1=dfFinalLocal.copy()
dfFinalNational.columns=dfFinalNational.columns.str.replace('_n','')
dfFinalNational1=dfFinalNational.copy()

In [ ]:
SC_Job_MappingBLS = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Supply_Chain_Job_Mapping.csv")

In [ ]:
SC_Job_MappingBLS =SC_Job_MappingBLS.toPandas()

In [ ]:
#dbutils.fs.mv('/FileStore/tables/Master_File_WM_Sams_HW_Field_Job_Mapping___Current-e3c17.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

In [ ]:
MasterBLSmap = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Master_File_WM_Sams_HW_Field_Job_Mapping___Current-e3c17.csv")

In [ ]:
MasterBLSmap=MasterBLSmap.toPandas()

In [ ]:
SC_Job_MappingBLS=SC_Job_MappingBLS.merge(MasterBLSmap,left_on='Job Code',right_on='Company Job Code',how='inner')

In [ ]:
SC_Job_MappingBLS=SC_Job_MappingBLS[['Job Code','SOC']]

In [ ]:
dfFinalNational1=dfFinalNational1.merge(SC_Job_MappingBLS,left_on='JobCode',right_on='Job Code',how='inner')

In [ ]:
dfFinalNational1.columns

Out[ 67 ]: Index(['Location', 'JobCode', 'Base_low_10.0', 'Base_low_25.0',
 'Base_low_50.0', 'Base_low_75.0', 'Base_low_90.0', 'TCC_low_10.0',
 'TCC_low_25.0', 'TCC_low_50.0', 'TCC_low_75.0', 'TCC_low_90.0',
 'TDC_low_10.0', 'TDC_low_25.0', 'TDC_low_50.0', 'TDC_low_75.0',
 'TDC_low_90.0', 'Base_mid_10.0', 'Base_mid_25.0', 'Base_mid_50.0',
 'Base_mid_75.0', 'Base_mid_90.0', 'TCC_mid_10.0', 'TCC_mid_25.0',
 'TCC_mid_50.0', 'TCC_mid_75.0', 'TCC_mid_90.0', 'TDC_mid_10.0',
 'TDC_mid_25.0', 'TDC_mid_50.0', 'TDC_mid_75.0', 'TDC_mid_90.0',
 'Base_high_10.0', 'Base_high_25.0', 'Base_high_50.0', 'Base_high_75.0',
 'Base_high_90.0', 'TCC_high_10.0', 'TCC_high_25.0', 'TCC_high_50.0',
 'TCC_high_75.0', 'TCC_high_90.0', 'TDC_high_10.0', 'TDC_high_25.0',
 'TDC_high_50.0', 'TDC_high_75.0', 'TDC_high_90.0', 'Job Code', 'SOC'],
 dtype='object')

In [ ]:
#dbutils.fs.mv('/FileStore/tables/BLS_Data-cd57f.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

In [ ]:
BLSData = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/BLS_Data-cd57f.csv")

In [ ]:
BLSData=BLSData.toPandas()

In [ ]:
BLSData=BLSData[['area_title','area_type','naics_title','occ_code','a_mean','mean_prse']]

In [ ]:
BLSData=BLSData[(BLSData.naics_title =='Cross-industry') & (BLSData.area_type != 2)]

In [ ]:
BLSData['LIndicator']=BLSData['area_type'].apply(lambda x: 'National' if x==1 else "Local")

In [ ]:
BLSData=BLSData.replace(r'\*',np.nan,regex=True)
BLSData=BLSData.replace(r'\#',np.nan,regex=True)
BLSData=BLSData.replace(r'\,','',regex=True)

In [ ]:
BLSData=BLSData.fillna(0)

In [ ]:
BLSData[['a_mean','mean_prse']]=BLSData[['a_mean','mean_prse']].apply(pd.to_numeric)

In [ ]:
BLSData['LBound']=BLSData.apply(lambda x: x['a_mean']*(1-x['mean_prse']/100),axis=1)
BLSData['HBound']=BLSData.apply(lambda x: x['a_mean']*(1+x['mean_prse']/100),axis=1)

In [ ]:
BLSDataN=BLSData[BLSData['LIndicator']=='National']
BLSDataL=BLSData[BLSData['LIndicator']!='National']


In [ ]:
BLSDataN=BLSDataN.merge(BLSDataL,left_on='occ_code',right_on='occ_code',how='inner')

In [ ]:
BLSDataN=BLSDataN.rename(columns={'area_title_x':'area_title_national', 'area_type_x':'area_type_national', 'naics_title_x':'naics_title_national', 'a_mean_x' :'a_mean_national','mean_prse_x':'mean_prse_national', 'LIndicator_x':'LIndicator_national', 'LBound_x':'LBound_national' , 'HBound_x':'HBound_national', 'area_title_y':'area_title_local','area_type_y':'area_type_local', 'naics_title_y':'naics_title_local', 'a_mean_y':'a_mean_local', 'mean_prse_y':'mean_prse_local', 'LIndicator_y':'LIndicator_local', 'LBound_y':'LBound_local', 'HBound_y':'HBound_local'})

In [ ]:
BLSDataN=BLSDataN[(BLSDataN.LBound_local !=0) & (BLSDataN.HBound_local !=0)]

In [ ]:
def ratiocal(LBound_local,HBound_national,LBound_national,HBound_local):
  val1=LBound_local/HBound_national
  val2=HBound_local/LBound_national
  val3=[val1,val2]
  return statistics.mean(val3)

In [ ]:
BLSDataN['Ratio']=BLSDataN.apply(lambda x: ratiocal(x['LBound_local'],x['HBound_national'],x['LBound_national'],x['HBound_local']),axis=1)

In [ ]:
BLSDatat=BLSDataN.merge(dfFinalNational1,left_on='occ_code',right_on='SOC',how='inner')

In [ ]:
cols = [i for i in BLSDatat.columns if i not in ['area_title_national', 'area_type_national', 'naics_title_national',
       'occ_code', 'a_mean_national', 'mean_prse_national',
       'LIndicator_national', 'LBound_national', 'HBound_national',
       'area_title_local', 'area_type_local', 'naics_title_local',
       'a_mean_local', 'mean_prse_local', 'LIndicator_local', 'LBound_local',
       'HBound_local', 'Location', 'JobCode','SOC','Job Code']]

In [ ]:
BLSDatat[cols]=BLSDatat[cols].apply(lambda x:x[cols]*x['Ratio'] ,axis=1)

In [ ]:
BLSDatat=BLSDatat[['area_title_local', 'JobCode', 'Base_low_10.0',
       'Base_low_25.0', 'Base_low_50.0', 'Base_low_75.0', 'Base_low_90.0',
       'TCC_low_10.0', 'TCC_low_25.0', 'TCC_low_50.0', 'TCC_low_75.0',
       'TCC_low_90.0', 'TDC_low_10.0', 'TDC_low_25.0', 'TDC_low_50.0',
       'TDC_low_75.0', 'TDC_low_90.0', 'Base_mid_10.0', 'Base_mid_25.0',
       'Base_mid_50.0', 'Base_mid_75.0', 'Base_mid_90.0', 'TCC_mid_10.0',
       'TCC_mid_25.0', 'TCC_mid_50.0', 'TCC_mid_75.0', 'TCC_mid_90.0',
       'TDC_mid_10.0', 'TDC_mid_25.0', 'TDC_mid_50.0', 'TDC_mid_75.0',
       'TDC_mid_90.0', 'Base_high_10.0', 'Base_high_25.0', 'Base_high_50.0',
       'Base_high_75.0', 'Base_high_90.0', 'TCC_high_10.0', 'TCC_high_25.0',
       'TCC_high_50.0', 'TCC_high_75.0', 'TCC_high_90.0', 'TDC_high_10.0',
       'TDC_high_25.0', 'TDC_high_50.0', 'TDC_high_75.0', 'TDC_high_90.0']]

In [ ]:
#Reading the facility CBSA mapping file
#dbutils.fs.mv('/FileStore/tables/Faciities_CBSA_MSAname.csv','/mnt/totalrewards/dev/adhoc/a0a025e/')

In [ ]:
Facility_CBSA_Mapping = spark.read.format("csv")\
  .option("header", "true")\
  .option("inferSchema", "true")\
  .load("/mnt/totalrewards/dev/adhoc/a0a025e/Faciities_CBSA_MSAname.csv")

Facility_CBSA_Mapping=Facility_CBSA_Mapping.toPandas()


In [ ]:

#Merging Facility mapping with blended local data on CBSA Title
Facility_level_data1 = dfFinalLocal1.merge(Facility_CBSA_Mapping[['Facility','CBSA Title','May 2018 MSA name','City','State_Name','Zip Code']],left_on='Location',right_on='CBSA Title',how='inner')
                                                                 
Facility_level_data1['CalculationType']='DirectMatch'
                                                               
#Facility_level_data1=Facility_level_data1['Facility'].unique()
Facility_level_data1=Facility_level_data1.groupby('Facility').first()      
Facility_level_data1.reset_index(level=0, inplace=True)

Facility_level_data1.shape

Out[ 88 ]: (2785, 56)

In [ ]:
#Getting the unmatched locations from facility cbsa mapping based on CBSA title
Facility_level_data_unmatched1 = Facility_CBSA_Mapping[['Facility','CBSA Title','May 2018 MSA name','City','State_Name','Zip Code']].merge(Facility_level_data1[['Location']],left_on='CBSA Title',right_on='Location', how = 'outer' ,indicator=True).loc[lambda x : x['_merge']=='left_only']
Facility_level_data_unmatched1 = Facility_level_data_unmatched1.drop(['_merge'], axis = 1)
Facility_level_data_unmatched1.shape

Out[ 90 ]: (7559, 7)

In [ ]:
Facility_level_data_unmatched1.columns

Out[ 91 ]: Index(['Facility', 'CBSA Title', 'May 2018 MSA name', 'City', 'State_Name',
 'Zip Code', 'Location'],
 dtype='object')

In [ ]:
#Joining the unmatched locations on May 2018 MSA name (BLS Location)
Facility_level_data2 = Facility_level_data_unmatched1[['Facility','CBSA Title','May 2018 MSA name','State_Name','City','Zip Code']].merge(dfFinalLocal1,left_on='May 2018 MSA name',right_on='Location',how='inner')
Facility_level_data2['CalculationType']='DirectMatch'

Facility_level_data2=Facility_level_data2.groupby('Facility').first()      
Facility_level_data2.reset_index(level=0, inplace=True)
Facility_level_data2.shape

Out[ 92 ]: (34, 56)

In [ ]:
#Getting the unmatched locations from facility cbsa mapping based on May 2018 MSA name (BLS Location)
Facility_level_data_unmatched2 = Facility_level_data_unmatched1[['Facility','CBSA Title','May 2018 MSA name','City','State_Name','Zip Code']].merge(Facility_level_data2[['Location']],left_on='May 2018 MSA name',right_on='Location', how = 'outer' ,indicator=True).loc[lambda x : x['_merge']=='left_only']
Facility_level_data_unmatched2 = Facility_level_data_unmatched2.drop(['_merge'], axis = 1)
Facility_level_data_unmatched2.shape

Out[ 93 ]: (7525, 7)

In [ ]:
#Joining the unmatched locations with BLS data
Facility_level_data3 = Facility_level_data_unmatched2[['Facility','CBSA Title','May 2018 MSA name','State_Name','City','Zip Code']].merge(BLSDatat,left_on='May 2018 MSA name',right_on='area_title_local',how='inner')
Facility_level_data3['CalculationType']='Relativity'
Facility_level_data3=Facility_level_data3.rename(columns={'area_title_local':'Location'})
Facility_level_data3=Facility_level_data3.groupby('Facility').first()      
Facility_level_data3.reset_index(level=0, inplace=True)
Facility_level_data3.shape

Out[ 94 ]: (1630, 54)

In [ ]:
frames=[Facility_level_data1,Facility_level_data2,Facility_level_data3]
Facility_level_data=pd.concat(frames)
Facility_level_data.shape

Out[ 95 ]: (4449, 56)

In [ ]:
dfFinalLocal1['Survey Aged Date']=Ageing_date
dfFinalLocal1['Survey Aged Date']=pd.to_datetime(dfFinalLocal1['Survey Aged Date']).dt.date
#dfs_local=sqlContext.createDataFrame(dfFinalLocal1)
#dfs_local.registerTempTable('Blended_Local')

dfFinalNational1['Survey Aged Date']=Ageing_date
dfFinalNational1['Survey Aged Date']=pd.to_datetime(dfFinalLocal1['Survey Aged Date']).dt.date
dfFinalNational1=dfFinalNational1.drop(['Job Code','SOC'],axis=1)
#dfs_national=sqlContext.createDataFrame(dfFinalNational1)
#dfs_national.registerTempTable('Blended_National')

#Merging local nad national data
dfFinal1=pd.concat([dfFinalLocal1,dfFinalNational1])
dfs_merged=sqlContext.createDataFrame(dfFinal1)
dfs_merged.registerTempTable('Supply_Chain_Blended')


In [ ]:
%sql
select * from Supply_Chain_Blended

Base_high_10.0 Base_high_25.0 Base_high_50.0 Base_high_75.0 Base_high_90.0 Base_low_10.0 Base_low_25.0 Base_low_50.0 Base_low_75.0 Base_low_90.0 Base_mid_10.0 Base_mid_25.0 Base_mid_50.0 Base_mid_75.0 Base_mid_90.0 Imputed TCC Imputed TDC JobCode Location Survey Aged Date TCC_high_10.0 TCC_high_25.0 TCC_high_50.0 TCC_high_75.0 TCC_high_90.0 TCC_low_10.0 TCC_low_25.0 TCC_low_50.0 TCC_low_75.0 TCC_low_90.0 TCC_mid_10.0 TCC_mid_25.0 TCC_mid_50.0 TCC_mid_75.0 TCC_mid_90.0 TDC_high_10.0 TDC_high_25.0 TDC_high_50.0 TDC_high_75.0 TDC_high_90.0 TDC_low_10.0 TDC_low_25.0 TDC_low_50.0 TDC_low_75.0 TDC_low_90.0 TDC_mid_10.0 TDC_mid_25.0 TDC_mid_50.0 TDC_mid_75.0 TDC_mid_90.0 111027.73 112762.5 112762.5 124472.7036 124472.7036 111027.73 111027.73 112762.5 112762.5 124472.7036 111027.73 111895.11499999999 112762.5 118617.6018 124472.7036 0.0 0.0 100012538 Akron, OH 2020-06-01 123599.58 127681.8895 127681.8895 142964.1438 142964.1438 123599.58 123599.58 127681.8895 127681.8895 142964.1438 123599.58 125640.73475 127681.8895 135323.01665 142964.1438 123599.58 127681.8895 127681.8895 142964.1438 142964.1438 123599.58 123599.58 127681.8895 127681.8895 142964.1438 123599.58 125640.73475 127681.8895 135323.01665 142964.1438 121565.11 121565.11 155308.9443 157133.0 165000.0 115000.0 121565.11 155308.9443 157133.0 157133.0 118282.555 121565.11 155308.9443 157133.0 161066.5 0.0 0.0 100012538 Albany-Schenectady-Troy, NY 2020-06-01 145878.132 145878.132 189309.7443 199562.3746 209655.0 138000.0 145878.132 189309.7443 199562.3746 199562.3746 141939.066 145878.132 189309.7443 199562.3746 204608.6873 145878.132 145878.132 189309.7443 199562.3746 209655.0 138000.0 145878.132 189309.7443 199562.3746 199562.3746 141939.066 145878.132 189309.7443 199562.3746 204608.6873 117810.24 117810.24 128600.16 138357.7698 164000.0 113600.0 117810.24 128600.16 138357.7698 138357.7698 115705.12 117810.24 128600.16 138357.7698 151178.8849 0.0 0.0 100012538 Athens-Clarke County, GA 2020-06-01 141789.2736 141789.2736 154320.192 171487.9692 205000.0 135187.5 141789.2736 154320.192 171487.9692 171487.9692 138488.38679999998 141789.2736 154320.192 171487.9692 188243.9846 141789.2736 141789.2736 154320.192 171487.9692 205000.0 135187.5 141789.2736 154320.192 171487.9692 171487.9692 138488.38679999998 141789.2736 154320.192 171487.9692 188243.9846 119000.0 119000.0 135589.6662 150000.0 150000.0 106996.032 119000.0 130000.0 135589.6662 150000.0 112998.016 119000.0 132794.8331 142794.8331 150000.0 0.0 0.0 100012538 Atlanta-Sandy Springs-Alpharetta, GA 2020-06-01 139675.0 140399.2064 161918.3586 184209.714 184209.714 127671.032 139675.0 156000.0 162247.051 184209.714 133673.016 140037.1032 158959.1793 173228.3825 184209.714 139675.0 140399.2064 161918.3586 184209.714 184209.714 127671.032 139675.0 156000.0 162247.051 184209.714 133673.016 140037.1032 158959.1793 173228.3825 184209.714 126860.75 130305.0816 130305.0816 143217.7436 143217.7436 126860.75 126860.75 130305.0816 130305.0816 143217.7436 126860.75 128582.9158 130305.0816 136761.41259999998 143217.7436 0.0 0.0 100012538 Baltimore-Columbia-Towson, MD 2020-06-01 148788.5684 153295.1754 153295.1754 172804.5833 172804.5833 148788.5684 148788.5684 153295.1754 153295.1754 172804.5833 148788.5684 151041.8719 153295.1754 163049.87935 172804.5833 148788.5684 153295.1754 153295.1754 172804.5833 172804.5833 148788.5684 148788.5684 153295.1754 153295.1754 172804.5833 148788.5684 151041.8719 153295.1754 163049.87935 172804.5833 109268.64 109268.64 125713.0 126264.3576 139050.08 96470.4 109268.64 125713.0 126264.3576 126264.35760000002 102869.51999999999 109268.64 125713.0 126264.3576 132657.2188 0.0 0.0 100012538 Boulder, CO 2020-06-01 131122.368 131122.368 150855.6 153050.2566 172356.0 110940.96 131122.368 150855.6 153050.2566 153050.25660000002 121031.66399999999 131122.368 150855.6 153050.2566 162703.1283 131122.368 131122.368 150855.6 153050.2566 172356.0 110940.96 131122.368 150855.6 153050.2566 153050.25660000002 121031.6639999999

In [ ]:
dfFacilityLevel=sqlContext.createDataFrame(Facility_level_data)
dfFacilityLevel.registerTempTable('Supply_Chain_FacilityLevel')


In [ ]:
%sql
Select * from Supply_Chain_FacilityLevel

Base_high_10.0 Base_high_25.0 Base_high_50.0 Base_high_75.0 Base_high_90.0 Base_low_10.0 Base_low_25.0 Base_low_50.0 Base_low_75.0 Base_low_90.0 Base_mid_10.0 Base_mid_25.0 Base_mid_50.0 Base_mid_75.0 Base_mid_90.0 CBSA Title CalculationType City Facility Imputed TCC Imputed TDC JobCode Location May 2018 MSA name State_Name TCC_high_10.0 TCC_high_25.0 TCC_high_50.0 TCC_high_75.0 TCC_high_90.0 TCC_low_10.0 TCC_low_25.0 TCC_low_50.0 TCC_low_75.0 TCC_low_90.0 TCC_mid_10.0 TCC_mid_25.0 TCC_mid_50.0 TCC_mid_75.0 TCC_mid_90.0 TDC_high_10.0 TDC_high_25.0 TDC_high_50.0 TDC_high_75.0 TDC_high_90.0 TDC_low_10.0 TDC_low_25.0 TDC_low_50.0 TDC_low_75.0 TDC_low_90.0 TDC_mid_10.0 TDC_mid_25.0 TDC_mid_50.0 TDC_mid_75.0 TDC_mid_90.0 Zip Code 74381.008 74381.008 89846.016 92394.8733 113300.0 67530.944 74381.008 79011.92 89846.016 92394.8733 70955.976 74381.008 84428.968 91120.44465 102847.43665 Kansas City, MO-KS DirectMatch Leavenworth 26 0.0 0.0 100012555 Kansas City, MO-KS Kansas City, MO-KS Kansas 75381.72499999999 82284.992 102665.3247 105214.182 132609.375 68531.661 75381.72499999999 86915.904 102665.3247 105214.182 71956.69299999998 78833.3585 94790.61434999999 103939.75335 118911.7785 75381.72499999999 82284.992 102665.3247 105214.182 132609.375 68531.661 75381.72499999999 86915.904 102665.3247 105214.182 71956.69299999998 78833.3585 94790.61434999999 103939.75335 118911.7785 66048.0 69694.0 69694.0 72197.3647 82000.0 89914.0 59000.0 69694.0 72197.3647 82000.0 82000.0 64347.0 69694.0 72197.3647 82000.0 85957.0 St. Louis, MO-IL DirectMatch Troy 60 0.0 0.0 100012564 St. Louis, MO-IL St. Louis, MO-IL Missouri 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 63379.0 69694.0 69694.0 72197.3647 82000.0 89914.0 59000.0 69694.0 72197.3647 82000.0 82000.0 64347.0 69694.0 72197.3647 82000.0 85957.0 St. Louis, MO-IL DirectMatch Sullivan 65 0.0 0.0 100012564 St. Louis, MO-IL St. Louis, MO-IL Missouri 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 63080.0 69694.0 69694.0 72197.3647 82000.0 89914.0 59000.0 69694.0 72197.3647 82000.0 82000.0 64347.0 69694.0 72197.3647 82000.0 85957.0 St. Louis, MO-IL DirectMatch Festus 69 0.0 0.0 100012564 St. Louis, MO-IL St. Louis, MO-IL Missouri 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 73881.3792 76663.4 80424.364 90428.0 98414.0 63187.379199999996 73881.3792 79166.7647 90226.9993 90428.0 68534.3792 75272.3896 79795.56435 90327.49965 94421.0 63028.0 74381.008 74381.008 89846.016 92394.8733 113300.0 67530.944 74381.008 79011.92 89846.016 92394.8733 70955.976 74381.008 84428.968 91120.44465 102847.43665 Kansas City, MO-KS DirectMatch Harrisonville 96 0.0 0.0 100012555 Kansas City, MO-KS Kansas City, MO-KS Missouri 75381.72499999999 82284.992 102665.3247 105214.182 132609.375 68531.661 75381.72499999999 86915.904 102665.3247 105214.182 71956.69299999998 78833.3585 94790.61434999999 103939.75335 118911.7785 75381.72499999999 82284.992 102665.3247 105214.182 132609.375 68531.661 75381.72499999999 86915.904 102665.3247 105214.182 71956.69299999998 78833.3585 94790.61434999999 103939.75335 118911.7785 64701.0 69694.0 69694.0 72197.3647 82000.0 89914.0 59000.0 69694.0 72197.3647 82000.0 82000.0 64347.0 69694.0 72197.3647 82000.0 85957.0 St. Louis, MO-IL DirectMatch Union 99 0.0 0.0 100012564 St. Louis, MO-IL St. Louis, MO-IL Missouri 73881.3792 76663.4 80424.364 90428.0 98414.0

In [ ]:
dfBLSGeoRelativity=sqlContext.createDataFrame(BLSDatat)
dfBLSGeoRelativity.registerTempTable('Supply_Chain_BLSGeographyRelativity')


In [ ]:
%sql
select * from Supply_Chain_BLSGeographyRelativity

area_title_local JobCode Base_low_10.0 Base_low_25.0 Base_low_50.0 Base_low_75.0 Base_low_90.0 TCC_low_10.0 TCC_low_25.0 TCC_low_50.0 TCC_low_75.0 TCC_low_90.0 TDC_low_10.0 TDC_low_25.0 TDC_low_50.0 TDC_low_75.0 TDC_low_90.0 Base_mid_10.0 Base_mid_25.0 Base_mid_50.0 Base_mid_75.0 Base_mid_90.0 TCC_mid_10.0 TCC_mid_25.0 TCC_mid_50.0 TCC_mid_75.0 TCC_mid_90.0 TDC_mid_10.0 TDC_mid_25.0 TDC_mid_50.0 TDC_mid_75.0 TDC_mid_90.0 Base_high_10.0 Base_high_25.0 Base_high_50.0 Base_high_75.0 Base_high_90.0 TCC_high_10.0 TCC_high_25.0 TCC_high_50.0 TCC_high_75.0 TCC_high_90.0 TDC_high_10.0 TDC_high_25.0 TDC_high_50.0 TDC_high_75.0 TDC_high_90.0 Guam 100012538 49206.04837437342 57830.41447217398 69233.3551439314 73270.56301553243 81624.97895599592 54235.36738677792 68020.31415447709 82497.6482894371 88143.20497087519 99474.97217273727 54235.36738677792 68020.31415447709 82497.6482894371 88143.20497087519 99474.97217273727 53518.231423273704 57830.41447217398 71251.95907973191 77447.77098576417 88399.86774807934 61127.84077062751 68020.31415447709 85320.42663015614 93809.08857180623 109051.11950320027 61127.84077062751 68020.31415447709 85320.42663015614 93809.08857180623 109051.11950320027 57830.41447217398 57830.41447217398 73270.56301553243 81624.97895599592 95174.75654016277 68020.31415447709 68020.31415447709 88143.20497087519 99474.97217273727 118627.26683366328 68020.31415447709 68020.31415447709 88143.20497087519 99474.97217273727 118627.26683366328 Guam 100012539 49206.04837437342 57830.41447217398 69233.3551439314 73270.56301553243 81624.97895599592 54235.36738677792 68020.31415447709 82497.6482894371 88143.20497087519 99474.97217273727 54235.36738677792 68020.31415447709 82497.6482894371 88143.20497087519 99474.97217273727 53518.231423273704 57830.41447217398 71251.95907973191 77447.77098576417 88399.86774807934 61127.84077062751 68020.31415447709 85320.42663015614 93809.08857180623 109051.11950320027 61127.84077062751 68020.31415447709 85320.42663015614 93809.08857180623 109051.11950320027 57830.41447217398 57830.41447217398 73270.56301553243 81624.97895599592 95174.75654016277 68020.31415447709 68020.31415447709 88143.20497087519 99474.97217273727 118627.26683366328 68020.31415447709 68020.31415447709 88143.20497087519 99474.97217273727 118627.26683366328 Guam 100012541 38187.919314174906 42744.47229103092 49780.20466076673 55846.90111948828 64019.59133803601 41432.49642996105 47354.29723365649 55825.12922705897 63180.06467769245 77132.98942622959 54800.37555326626 60722.1763569617 69193.00835036418 95187.75096333082 112063.39715507271 40466.19580260292 46262.338475898825 52813.55289012751 59933.24622876214 74877.06761051565 44393.39683180877 51589.71323035773 59502.59695237571 70156.52705196102 92069.22153404974 57761.27595511398 64957.59235366294 82190.37965684751 102164.21333759939 140151.87575731298 42744.47229103092 49780.20466076673 55846.90111948828 64019.59133803601 85734.54388299525 47354.29723365649 55825.12922705897 63180.06467769245 77132.98942622959 107005.45364186987 60722.1763569617 69193.00835036418 95187.75096333082 109140.67571186797 168240.35435955322 Guam 100012542 38187.919314174906 42744.47229103092 49780.20466076673 55846.90111948828 64019.59133803601 41432.49642996105 47354.29723365649 55825.12922705897 63180.06467769245 77132.98942622959 54800.37555326626 60722.1763569617 69193.00835036418 95187.75096333082 112063.39715507271 40466.19580260292 46262.338475898825 52813.55289012751 59933.24622876214 73496.95551968925 44393.39683180877 51589.71323035773 59502.59695237571 70156.52705196102 90689.10944322335 57761.27595511398 64957.59235366294 82190.37965684751 102164.21333759939 138771.7636664866 42744.47229103092 49780.20466076673 55846.90111948828 64019.59133803601 82974.31970134248 47354.29723365649 55825.12922705897 63180.06467769245 77132.98942622959 104245.22946021709 60722.1763569617 69193.00835036418 95187.75096333082 109140.67571186797 165480.13017790043 Guam 100012543 48146.87634907285 53546.350837